In [1]:
using Plots; plotlyjs();
using Mocha

Configuring Mocha...
 * CUDA       disabled by default
 * Native Ext disabled by default
Mocha configured, continue loading module...


DefaultBackend = Mocha.CPUBackend


<script type="text/x-mathjax-config">
  MathJax.Hub.Config({tex2jax: {inlineMath: [['$','$'], ['\\(','\\)']]}});
</script>
<script type="text/javascript"
  src="http://cdn.mathjax.org/mathjax/latest/MathJax.js?config=TeX-AMS-MML_HTMLorMML">
</script>


# Mocha.jl: 
## Deep Learning framework for Julia
<br><br>
### Alexander Amini

# What is Mocha.jl? 

<br>


<div>

    <p style="float: right;"><img src="https://camo.githubusercontent.com/e1ae5c7f6fe275a50134d5889a68f0acdd09ada8/687474703a2f2f6a756c69616c616e672e6f72672f696d616765732f6c6f676f5f68697265732e706e67" width="400px" /></p>
   
   <ul>
    <li> A **Deep Learning** framework for Julia </li>
    <li> Inspired by the C++ library, *Caffe* </li>
    <li> Quick prototyping of various deep architectures: 
        <ol>
            <li> Convolutional Neural Networks</li>
            <li> Recurrent Neural Networks</li>
            <li> Autoencoders</li>
            <li> ...and more</li>
        </ol>
    </li>
    


</div>


# Installation is simple!

Download the package - run once. 
>Pkg.add("Mocha");


In [2]:
using Mocha

# Can use the GPU:

In [3]:
#backend = GPUBackend() #use GPU
backend = CPUBackend() #use CPU
init(backend)

In [4]:
show(backend);

Mocha.CPUBackend

# Project Goal

<h4 align="center"><i>An optimization package to achieve immediate speedups over default SGD implementation</i></h4>
<div>

    <p style="float: right;"><img src="./imgs/flow.png" width="500px" /></p>
   
   <ul>
    <li> Improve naive optimizers implemented in Mocha </li>
    <li> Package new, accelerated optimization algorithms into the module </li>
    <li> Focus on code modulation and efficiency </li>
    
    </ul>.
    <br>
</div>



<h1 align="center">Vision:</h1>
<br>
<h3 align="center"><i>An optimization package that users can use instead of vanilla SGD to achieve immediate speedups</i></h3>



# Simple Learning Problem
<br>
Let's start by creating a new simple model to estimate the line of best fit from 2D data.
<br>

We begin by generating the dataset. In this example we will use 500 data-points

In [5]:
N = 500; # Number of data-points
(M,b) = (2,4); # Slope, Y-Intercept

X = linspace(1,2,N);
Ytrue = M.*X+b;
Y = Ytrue + randn(N)./10; # Add Gaussian Noise;

## We can visualize the training data

In [6]:
plot([1],t=:bar);

[Plots.jl] Initializing backend: plotlyjs
22-Oct 18:06:39:WARNING:root:Keyword argument bar_width not supported with Plots.PlotlyJSBackend().  Choose from: [:annotations,:background_color_legend,:background_color_inside,:background_color_outside,:foreground_color_legend,:foreground_color_guide,:foreground_color_text,:foreground_color_border,:foreground_color_title,:label,:seriescolor,:seriesalpha,:linecolor,:linestyle,:linewidth,:linealpha,:markershape,:markercolor,:markersize,:markeralpha,:markerstrokewidth,:markerstrokecolor,:markerstrokealpha,:markerstrokestyle,:fillrange,:fillcolor,:fillalpha,:bins,:title,:title_location,:titlefont,:window_title,:guide,:lims,:ticks,:scale,:flip,:rotation,:tickfont,:guidefont,:legendfont,:grid,:legend,:colorbar,:marker_z,:levels,:ribbon,:quiver,:orientation,:polar,:normalize,:weights,:hover,:inset_subplots,:color_palette,:background_color,:background_color_subplot,:foreground_color,:foreground_color_subplot,:group,:seriestype,:seriescolor,:seriesalp

In [7]:
plot(X, Ytrue, lab="Ground Truth"); 
scatter!(X, Y, marker=(0.5,2), lab="Input Data")

# Create Model
<br>
Define a single perceptron model with one weight and one bias to be learned.

In [8]:
data_layer = MemoryDataLayer(batch_size=1, data=Array[X,Y])
weight_layer = InnerProductLayer(name="ip",output_dim=1, tops=[:pred], bottoms=[:data])
loss_layer = SquareLossLayer(name="loss", bottoms=[:pred, :label])

net = Net("Single Perceptron", backend, [loss_layer, weight_layer, data_layer]);

22-Oct 18:06:49:INFO:root:Constructing net Single Perceptron on Mocha.CPUBackend...
22-Oct 18:06:49:INFO:root:Topological sorting 3 layers...
22-Oct 18:06:50:INFO:root:Setup layers...
22-Oct 18:06:51:INFO:root:Network constructed!


In [9]:
type Recorder <: Coffee
    loss::Vector{Float64};
    lr::Vector{Float64};
    
    w::Vector{Float64}; 
    b::Vector{Float64};
end

function Mocha.enjoy(lounge::CoffeeLounge, coffee::Recorder, net::Net, state::SolverState)
    push!(coffee.loss, state.obj_val);
    push!(coffee.lr, state.internal.learning_rate);
    
    weight = state.internal.param_states[1].parameters[1].blob.data[1];
    bias = state.internal.param_states[1].parameters[2].blob.data[1];
        
    push!(coffee.w, weight)
    push!(coffee.b, bias)
end

enjoy (generic function with 5 methods)

# Setup our optimizer

In [10]:
method = SGD(); 
params = make_solver_parameters(method, max_iter=10000)
solver = Solver(method, params)
r = Recorder([],[],[],[]); add_coffee_break(solver, r, every_n_iter=1)

INSIDE make_solver_parameters of SGD


1-element Array{Mocha.CoffeeBreak,1}:
 Mocha.CoffeeBreak(Recorder(Float64[],Float64[],Float64[],Float64[]),1,0)

# Solve!

In [11]:
solve(solver, net);
println(); @printf "Converged. Estimated=(%f,%f). Actual=(%f,%f)" r.w[end] r.b[end] M b

22-Oct 18:06:56:DEBUG:root:#DEBUG Checking network topology for back-propagation
22-Oct 18:06:56:DEBUG:root:Init network Single Perceptron
22-Oct 18:06:56:DEBUG:root:Init parameter weight for layer ip
22-Oct 18:06:56:DEBUG:root:Init parameter bias for layer ip
22-Oct 18:06:57:DEBUG:root:#DEBUG Initializing coffee breaks
22-Oct 18:06:57:DEBUG:root:#DEBUG Entering solver loop

Converged. Estimated=(2.219806,3.583981). Actual=(2.000000,4.000000)

# But how did the optimization occur?

### Stochastic Gradient Descent 

Update Equation: $\theta_{t+1} = \theta_t - \gamma \nabla L(\theta_t)$

Error Function: $L(\theta) = \frac{1}{2N}\sum \parallel y(\theta) - \hat y \parallel^2$

In [12]:
method = SGD() 

Mocha.SGD()

In [13]:
mv = linspace(M-4,M+4,100);
bv = linspace(b-4,b+4,100);


MV = repmat(mv',length(bv),1);
BV = repmat(bv,1,length(mv));

# Visualize the Gradient Descent

In [32]:
loss(x,y) = sum(((x.*X+y)-Y).^2)/(2*N)
Z = map(loss,MV,BV);

plot( surface(mv,bv,loss,fill=true,levels=30), 
      plot3d(r.w,r.b,map(loss,r.w,r.b),line=8) )

# Or in 2D...

In [30]:
contour(mv,bv,loss,fill=true,levels=20, xaxis="weight", yaxis="bias");
plot!(r.w,r.b,line=5)

# Loss (error) function minimization over iterations 

In [16]:
plot(r.loss,xaxis=("Iterations",:log),yaxis=("Loss"),lab="")

# Why should we care about SGD?



<div>

    <p style="float: right;"><img src="http://cs231n.github.io/assets/nn3/learningrates.jpeg" width="400px" /></p>
   
    <ul>
    
    <li> More efficient optimizers could reduce training times </li>
    <li> Especially in very deep neural networks could make huge differences </li>
    <li> Algorithm that adapts according to the data topology </li>
    </ul>


</div>

# 18.377 Midterm Project

Create extension to Mocha.jl that allows users to optimize their deep networks at greater rates compared to current offerings in the package.

This project implements two new optimizers classes in Julia modulated within Mocha.jl: 

# Adagrad


<div>
    <p style="float: right;"><img src="./imgs/adagrad_crop.png" width="500px" /></p>
    <br><br><br><br>
   
   $$\theta_{t+1} = \theta_t - \frac{\gamma}{ \sqrt{\sum \nabla L(\theta_t)^2}} \nabla L(\theta_t)$$

</div>


In [17]:
method = Adagrad() 
params = make_solver_parameters(method, gamma=1.0)

Dict{Symbol,Any} with 5 entries:
  :regu_coef => 0.0005
  :load_from => ""
  :max_iter  => Inf
  :epsilon   => 1.0e-8
  :gamma     => 1.0

# Adadelta


<div>
    <p style="float: right;"><img src="./imgs/adadelta_crop.png" width="500px" /></p>
    <br><br>
   

    $$h_t = (1-\rho) \nabla L(\theta_t)^2 + \rho h_{t-1}$$
    $$\gamma_t = \sqrt{\frac{s_{t-1}+\epsilon}{h_{t}+\epsilon}}$$
    $$s_t = (1-\rho) \gamma_t^2 + \rho s_{t-1}$$
    $$\theta_{t+1} = \theta_t - \gamma_t$$

</div>

In [18]:
method = Adadelta() 
params = make_solver_parameters(method, rho=0.95, eps=1e-6)

Dict{Symbol,Any} with 5 entries:
  :regu_coef => 0.0005
  :rho       => 0.95
  :load_from => ""
  :eps       => 1.0e-6
  :max_iter  => Inf

# Deeper Look


<div>
    <p style="float: left;">
        <br><font size="5">Adagrad: </font><br> 
        <img src="./imgs/adagrad_code.png" width="460px" />
    </p>
    <p style="float: right;">
        <font size="5">Adadelta: </font><br> 
        <img src="./imgs/adadelta_code.png" width="460px" />
    </p>
</div>

# MNIST

Attempt to recognize handwritten digits using a deep convolutional neural network. 
    <center>
    <img src="https://ccjou.files.wordpress.com/2013/05/digits.png" align="middle" width="700px" />
</center>


In [19]:
digit=[0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.4,    0.6,    0.7,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.4,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.2,    0.1,    0.1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.3,    0.1,    0.2,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.2,    0.5,    0.5,0,0,0,0,0,0,0,0,    0.2,    0.1,    0.2,    0.7,0,0,0,0,0,0,0,0,0,0,0,    0.6,    0.6,    0.0,    0.1,    0.1,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.8,0,0,0,0,0,0,0,0,0,    0.8,    0.0,    0.4,    0.1,    0.1,    0.1,    0.8,0,0,0,0,0,0,0,0,0,    0.5,    0.4,    0.9,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.1,    0.1,    0.1,    0.1,    0.8,    0.6,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.7,0,0,0,0,0,0,0,    0.1,    0.7,    0.1,    0.1,    0.0,    0.9,    0.9,    0.9,0,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.7,0,0,0,0,0,    0.3,    0.1,    0.3,    0.1,    0.8,    0.0,    0.9,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.7,0,0,0,    0.4,    0.6,    0.9,    0.1,    0.2,    0.0,    0.3,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.4,    0.4,0,    0.3,    0.9,    0.5,    0.1,    0.5,    0.7,    0.5,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.0,    0.4,    0.5,    0.7,    0.1,    0.1,    0.3,    0.5,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.5,    0.1,    0.5,    0.2,    1.0,    0.3,    0.1,    0.6,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.7,    0.1,    0.1,    0.6,    0.5,    0.5,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,    0.9,    0.0,    0.7,    0.6,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0];
res1000=[2.36983060836792 2.36983060836792 2.36983060836792 2.36983060836792 2.36983060836792; 2.362575149536133 2.3560163974761963 2.336858129501343 2.3388720512390138 2.321275520324707; 2.353039531707764 2.3365618228912353 2.2873410987854004 2.2668083715438843 2.2371545219421387; 2.3481137981414797 2.3179665756225587 2.220213636398315 2.158753952026367 2.244267780303955; 2.3450477783203127 2.296569534301758 2.13057869644165 2.019298045349121 2.276529470062256; 2.328243689880371 2.2597634857177735 2.0090807674026485 1.8452165591812133 2.098348839263916; 2.316288580215454 2.231051545562744 1.8992383716659544 1.7095250024871826 1.8816165790405273; 2.301699344091797 2.2024566977996827 1.7758378456558226 1.6049292909683228 1.6666460407135009; 2.284546425957031 2.1637122511688234 1.6329382714053344 1.4855644406939699 1.4871973572061157; 2.2653994965700686 2.1226865434506226 1.4930934950844725 1.3565668584557498 1.3044173978078917; 2.2532459106563234 2.087431175220703 1.361769799004895 1.2280254222275513 1.1213271111097778; 2.23637859078397 2.0504585843950074 1.2462147264567236 1.1169005399800696 0.974229271399724; 2.2175802552870882 2.0050772938465724 1.1190862368652996 1.0187763385659343 0.8482356986902139; 2.1969779462951 1.9577755620746333 1.0205280431993626 0.9720097750573067 0.7540036874216384; 2.179180553065743 1.9157877437804953 0.9493077714354057 0.9818940615772174 0.7019577552637725; 2.1595144673244207 1.8667347091464055 0.881657065479776 0.8918619518374575 0.6362237695663189; 2.146536334678018 1.828959437849351 0.8058188808193372 0.8144198469237625 0.5702232769178561; 2.1299484605189036 1.7833302518862313 0.7531810960952892 0.7548196285499047 0.5293720166720718; 2.1121105380531846 1.7325422208418708 0.7021634786752425 0.6989504432307014 0.5119441708594775; 2.0934357983014342 1.6860462698070415 0.674049560978219 0.665574672669278 0.490027007315176; 2.079820755492954 1.646933315017081 0.7109019078844429 0.6564711116553198 0.49253815162469333; 2.061106612977432 1.5915285569971853 0.6606264406866742 0.618728221082755 0.4643427530788532; 2.044338433501758 1.5480097470717473 0.6542330499034653 0.5965571289253776 0.44789341289704254; 2.0235334861736596 1.4965506265987432 0.6316329690250977 0.5645105449352698 0.4114635721755442; 2.0088792028793576 1.4532927569094878 0.6302939059283911 0.5447937117412913 0.38974378593066666; 1.9896257307345775 1.4102523800805076 0.6137118341085577 0.5304314566767397 0.35514932244856623; 1.9758189269872592 1.3712071321070085 0.6157438517854423 0.5307116566591408 0.3318257132755873; 1.9606202323414554 1.3381697290468129 0.6322181511915375 0.5420319842094538 0.3235600550641344; 1.9420666042310135 1.296568374103539 0.6321712961988964 0.5317243660922334 0.32369350470461256; 1.9248792603287805 1.2493471942474308 0.5950873201050217 0.5112051268764722 0.3326117740262175; 1.9062761366108028 1.2078456514779616 0.5835628990298792 0.49307740134782696 0.3325426674833794; 1.890904402712104 1.1720939345124475 0.5749895003609884 0.47582166515022206 0.33309366877483526; 1.8634201097322443 1.1122562819292634 0.5598281226295653 0.4496017565109705 0.3073899473794874; 1.8411552991734297 1.0618122405664514 0.5243489604583123 0.41974339046306414 0.2761850198943278; 1.8188368627442002 1.0220364599908505 0.5032912680618555 0.41037725931983793 0.26697415636689353; 1.800460048438158 0.9882688498087814 0.468362167605765 0.3886918030308215 0.23854211242366544; 1.785886365509865 0.9620514850289099 0.4612869561743795 0.37766414102924095 0.2246196977008876; 1.7687513497168519 0.9442515286183732 0.4962183905468034 0.39334766838560287 0.24491595321571802; 1.7445679638143141 0.9104061653118434 0.5008445678413429 0.3790118477631393 0.23662893051843623; 1.718692257671019 0.8774396125396968 0.4887083648252899 0.36792112047583125 0.2263616855934523; 1.7027049181210683 0.8512786463038827 0.4643555187073083 0.3516457609741709 0.20165644226433932; 1.685072717455839 0.8326552379239961 0.4901541275093342 0.35672754704227616 0.20906184922029258; 1.6686302879554549 0.8244881525126588 0.500502189183981 0.36294289755241527 0.2159241194357052; 1.649037826784652 0.819761124808589 0.5301221173483139 0.38015172543061937 0.2235376520816147; 1.629268589598498 0.8170511941583946 0.5172800252022748 0.3907558255349252 0.23739736547976015; 1.5990216517309834 0.7962884601332343 0.5076171977664952 0.3909726328019026 0.28358365909981154; 1.5822051830180874 0.7844465133649187 0.5216616092797854 0.39587822249442123 0.3180210853952362; 1.5660962396533005 0.7578029797158301 0.5010883449456484 0.38166419618058034 0.298554834949032; 1.5367613262868494 0.7207571518962909 0.45515961161783464 0.3551684872526155 0.26457384008332535; 1.5151643615513302 0.6980553470091286 0.4325359281820546 0.34435637245323075 0.24081876697670973; 1.4953152308105833 0.6820331257213166 0.42437124585489355 0.33506927450295937 0.2159770787559474; 1.4730104978274827 0.665438309640011 0.4273424175213172 0.33702235666749203 0.2082330603045245; 1.4685305973205187 0.6801097991707491 0.4564257404669439 0.36122239826391 0.21108980028963248; 1.4337943331649476 0.6704310776903285 0.44132977656239786 0.35008004663999764 0.1936036401918424; 1.413143502573218 0.6537110449563704 0.40811541026206427 0.3394004611858995 0.18725376259731397; 1.400785507281658 0.6476639343652123 0.38780914620853757 0.35041713584973583 0.20361894115962303; 1.36579506518049 0.6148226903560157 0.3453746974571331 0.3274964828849965 0.1890805850041526; 1.3592155132421093 0.6088864244367596 0.3426103901945578 0.32555253422746133 0.18417182283501762; 1.3480060461146226 0.6078515082475278 0.3475856909817876 0.33474179797561227 0.19008051230033984; 1.3241345455632678 0.5916811251542355 0.3314897997908927 0.32138478512121244 0.17617952077405255; 1.310278906058158 0.5810685772817442 0.34087209572260674 0.31968804998837314 0.1695984959508308; 1.2855236877051082 0.556861873000551 0.3171419723420548 0.3099859162461154 0.16572728931151454; 1.2733450928566525 0.5576509201762587 0.34950202692263976 0.31996177667708336 0.16754128777378896; 1.2634094555566842 0.5708576770017553 0.3483683466014358 0.3377650541808696 0.1676293134164341; 1.2402278581770367 0.5608702446134892 0.35884809486842895 0.3302948842641903 0.16370603497596803; 1.2194862683226353 0.5534186955382034 0.3565556048772871 0.3276024516580258 0.16908750280358176; 1.1865869776097684 0.5305649217835748 0.3324626844662142 0.30868995337945254 0.1544378531544827; 1.171697760875046 0.5345515391724653 0.33057037087581254 0.31988877772698426 0.15486992757077395; 1.163275285764551 0.5516890948214012 0.3374278373901184 0.33302924608715073 0.16238680371090078; 1.153472506367378 0.5575132183391156 0.31413942693743196 0.3206624196015016 0.15196444005524556; 1.1218167609876097 0.5666651576485874 0.3025576302931554 0.3127929890984071 0.14435293901567015; 1.097699909759021 0.5589804768345071 0.28568233982927377 0.3064451595015345 0.14444848599914195; 1.0772456283191492 0.5517824864213716 0.27762311447625776 0.30065094867285236 0.15796954097655203; 1.0509485884364167 0.5272325377325258 0.2526266316490604 0.28579967470118317 0.16333987345144577; 1.0421058880373413 0.5189945181735389 0.24924730677741636 0.28654190898854665 0.1871845108655725; 1.044727829860415 0.5175442521197027 0.2646690203296174 0.29609441161886163 0.17368669816952023; 1.0320844632520405 0.5160804251370769 0.2574962531365577 0.29967859507191424 0.16227278120598057; 1.0211516842948698 0.5135279663036617 0.2707927290469506 0.2975838491963406 0.15694432860438712; 1.0173045337762279 0.5181876474722507 0.2886593988633234 0.3043143876113144 0.15627496664384752; 0.9930150938483748 0.4955069406115438 0.2688834111766878 0.2934639614993451 0.1431243745458901; 0.9777456984879711 0.4910656677312395 0.27110448208466076 0.299989778770933 0.14189931376558781; 0.9742722285558494 0.5008226527076356 0.27764417312157075 0.3101675422779159 0.15834907292351913; 0.9636062441483905 0.4916930352291578 0.2828823274899476 0.30599242343834526 0.1561356174868408; 0.9702312634957448 0.5148779634349436 0.2913919585171504 0.3238069883531848 0.16318464779234432; 0.9782305706797136 0.5268362310499264 0.31363197940374715 0.3319286601977761 0.1594806383321802; 0.9567775169418727 0.5236215589022885 0.3142106992227658 0.33049604076045475 0.15607415400108657; 0.9556340129698495 0.538722455308934 0.30867899157387607 0.3333629650107839 0.15409739523856608; 0.9371566892882331 0.5210205851444403 0.29130652207360735 0.31575764276439494 0.14170362967037176; 0.9181493974701679 0.5062785040099461 0.2794495197790946 0.30111367351098495 0.13705086096352748; 0.9113340025723867 0.5053599986043802 0.28499821803236686 0.31047489719616284 0.1354238401589903; 0.8852586464548821 0.49264804622389724 0.26734583859654015 0.3044405418795499 0.13855088140472674; 0.8707769407005879 0.4866909531820444 0.2509164038102766 0.29634876753188394 0.1391272724541418; 0.8633603011108854 0.4793210326090358 0.24671896777955213 0.290331436835108 0.13291545308608949; 0.8530957583218748 0.4721480129921358 0.23362660294697696 0.28617449294915026 0.12739336120668363; 0.8432325985932299 0.4667676900834975 0.23848430423677774 0.28030145916454174 0.12095344366696129; 0.8295076939983326 0.46525075952300526 0.22441456006956748 0.2780226171264027 0.1132369482681485; 0.8306299689231839 0.4672658258286245 0.2313169263759665 0.27377240063738617 0.11545056654336705; 0.8402307226513644 0.4818004936859709 0.23311767164543568 0.2927123940149291 0.12390211664297307; 0.8215339815024392 0.45889006025677537 0.22062884715140105 0.2782516687042986 0.11869394683963558; 0.8118461279395306 0.46053477102188756 0.2556749200577755 0.2999084936720113 0.14650605840783515; 0.8014573858835763 0.4570307352039694 0.24921204374275358 0.2971294619355186 0.1389845016463693; 0.7799194778329902 0.4393404954984569 0.2405891138397992 0.28739589931278103 0.13064977549426524; 0.7546593805413861 0.41906308605788417 0.22636414612001898 0.2713144489662542 0.11950534898370717; 0.7559704987415806 0.4178794163427215 0.22922239835792163 0.2733155483831321 0.12514391794467142; 0.7487389133937467 0.42383270167998166 0.24507952043003542 0.2842402513686303 0.12526074254245895; 0.7372387756162729 0.4106562273001011 0.24032872266440952 0.2771958633950141 0.12335882795835604; 0.7259082165760872 0.4069423068599173 0.23850554900860282 0.2786087870352099 0.12670179377385035; 0.7181155059657952 0.40603026660571645 0.2281965309579809 0.27596126435221274 0.13051062461048807; 0.7027971485394209 0.39147277404697856 0.21305235280193008 0.2628383631548964 0.12225993433642741; 0.6985587747206663 0.38027913157011767 0.19933339201289113 0.24577500780754746 0.11368574566879557; 0.6955701209156017 0.39013087180348793 0.2028999149233317 0.2538655885881858 0.11550231569797742; 0.709632130229338 0.4035571231610978 0.21701070423366353 0.26307739924007073 0.13411473865342893; 0.7040186896036975 0.40038914197026926 0.22111242517186583 0.25788992830605045 0.1333964169822753; 0.6877540408858388 0.3890325364537179 0.2094536831327548 0.24891768843722928 0.12097759104193215; 0.6664103793532634 0.37773047185477726 0.2011186508614437 0.24334738612804882 0.11525857394076161; 0.6632872523809261 0.38457591968009563 0.21668001042037138 0.2524367289593544 0.1146146501710953; 0.6693348170872361 0.39649081935270386 0.21109669328712566 0.26563583746359554 0.11418272072958484; 0.6669070745750928 0.38880650369154424 0.20818796492404257 0.2568604235633676 0.11278737248887646; 0.66249299250004 0.3816792759722631 0.2005763688626807 0.2500774947630933 0.10276118744937601; 0.6684075490789199 0.3961830213408598 0.1998236150696215 0.2610927413167613 0.10189748171590188; 0.6689980901206798 0.41935357449379995 0.18887191781634785 0.26247746668355126 0.10630104085701639; 0.670840845658403 0.4313353001906668 0.20352615530677395 0.2659430875150081 0.11117483489432284; 0.6803934702507823 0.4536170959340886 0.23222882243305648 0.27831765403490993 0.11997977346355397; 0.6584369285291171 0.42988987563986425 0.22447053446221515 0.26646455339703345 0.119252390266853; 0.6633574520258694 0.43326981901279166 0.23652690135517251 0.2818080243437559 0.12675293910614444; 0.6551594261096786 0.42792644333164753 0.2175183016703807 0.28384753322355516 0.11600057783215675; 0.6433427670611438 0.4145559249823957 0.20459526627431573 0.2808171093921071 0.11112526508163956; 0.6325322301398514 0.3962994657759404 0.18697164832886268 0.268291931784964 0.10162042440566657; 0.6222132612236976 0.3814618104938297 0.18704088830420343 0.25707143858020814 0.0955174266226549; 0.6121917143637847 0.3654167385294937 0.17027533841903184 0.24106480133490016 0.08604020318805847; 0.6111376583715209 0.3684874619162005 0.18453334007879235 0.2466186996456484 0.09584359877443054; 0.6084257483593566 0.3664875145845351 0.17324859586731703 0.24525028198214371 0.09021135461835654; 0.602727386960343 0.358526847051997 0.17708211193383622 0.24154219710232416 0.09137746874498201; 0.6220183878016118 0.3930821945567282 0.1921366079640459 0.26802065319539387 0.0967684641202837; 0.5960033701953604 0.3745144431034209 0.18741805247402757 0.2544216789541346 0.09566542891427277; 0.5819589747665178 0.3622357765229131 0.18118116968422388 0.24513991298180438 0.08970745663058279; 0.5857635699651917 0.3549153800321885 0.17634119958519343 0.23980538047871283 0.08553962864646528; 0.5887650817984168 0.35837137663469854 0.18028581238460067 0.2419104238154196 0.09307559794719389; 0.601410088567243 0.37701020212257813 0.1869117208057366 0.2509095040799541 0.09914187514015332; 0.5963674168811687 0.37138598419256935 0.1944630831665772 0.24629060668479308 0.10190598208290971; 0.6051630720318515 0.38189052945000274 0.20490807117517615 0.2592473009644421 0.11022592714295892; 0.6016612684584585 0.3741018128841904 0.20207761086222192 0.252823103818772 0.10555984233511376; 0.6022710351830265 0.3747612378954719 0.2096690553998682 0.2565319930342656 0.10564344350252856; 0.5871885298637979 0.3567505293655261 0.1927096411447313 0.24204206028205727 0.09459895247224419; 0.5787112735866254 0.35281955310248253 0.1801041138061354 0.2388877088516758 0.09254704101088404; 0.5629614073561625 0.34448957926863766 0.18352168773718433 0.2392710300040091 0.09288304792406367; 0.5634419503630794 0.3493661501950768 0.16645371149069277 0.24338370575522145 0.08720311172057951; 0.5565299894667941 0.3411853249030707 0.16492771788506672 0.23666349064520803 0.08105582687059851; 0.5451058790093484 0.32714464149136524 0.16353346156334053 0.2269150019583051 0.08555885358889748; 0.5546217477326252 0.33846648638454424 0.167954037565034 0.22898884720778023 0.09800592326513806; 0.5536374382976419 0.34124469641850275 0.18372687000277943 0.23440409785251265 0.1097723087739299; 0.5348562604430299 0.32708805111253964 0.16934391000464205 0.22268104223998741 0.10135182816357217; 0.5231055145456776 0.3162157480494555 0.17665211767828182 0.2165816906578728 0.09622907551980656; 0.5231382826959597 0.32357290542732686 0.16621760059098972 0.217847686687103 0.09626639565115484; 0.5214599831895437 0.3270927978087347 0.17943610671123322 0.22321563397168404 0.0962041014852946; 0.5341900598205254 0.33350486258895246 0.17123768367735906 0.22796422389602095 0.08888389274858038; 0.5256182977515161 0.32332438190961715 0.1596108099887241 0.21842695293788458 0.08190238634055934; 0.525074897524333 0.32102052537747094 0.16282218266085538 0.21563509021571753 0.08225835837369029; 0.5209434615108299 0.31996547912079387 0.1550591494127572 0.2149303042043962 0.08412964624122671; 0.5169949997689667 0.3204679587246442 0.15513907515879155 0.21289761727251355 0.0837149827238392; 0.513242341615863 0.32393995712291906 0.16306969041725541 0.22218179992991882 0.09398978221865266; 0.508615106374508 0.31507523091707 0.1555010488836014 0.21182478600468793 0.08383896365524744; 0.5168237805608796 0.3166540243790418 0.1545602082179422 0.21410319812080508 0.08714210820008449; 0.517503449936222 0.3164231164110398 0.1589215397013374 0.21428731566255288 0.08580889270153945; 0.5158178525126067 0.32338414055925174 0.16204443269357266 0.22593083767561115 0.09828877222893481; 0.5131840719347069 0.32446245918926847 0.16921330148685124 0.22131597827647526 0.0986619767336674; 0.5121763120941217 0.33201661165759766 0.17460348530378458 0.2264571116826884 0.10769336436499179; 0.49775885310585466 0.31878121659124536 0.1713557159802637 0.2173817278116506 0.11093045136776782; 0.4806940815195653 0.30179574263067754 0.16093268769195251 0.20581526825186108 0.10675983815548593; 0.4536358266151121 0.28500275251842905 0.14713083924619813 0.19546192403122978 0.0989776889614882; 0.45202726714421676 0.2779435421035875 0.13695921279405324 0.18676747294652618 0.0861691678172447; 0.44938651198235646 0.2732853039110652 0.125741616606035 0.18211960126867419 0.08487510936308684; 0.4431636371142665 0.2632438843651574 0.11563044992631132 0.17212963167755227 0.07722411657848981; 0.43741370144899683 0.25796962123743383 0.12058254943327469 0.16829024008058246 0.07177411451323054; 0.4419653606686274 0.2705810514420802 0.1333631713472713 0.1858564357053656 0.0815113191555597; 0.430633405230306 0.25850112715010126 0.12104644541207227 0.1751883061799541 0.0752892989715463; 0.43145365864583846 0.2604550717563969 0.11962013176491477 0.1760533090093243 0.07541302234335948; 0.4475451457544088 0.27687068568003514 0.12150955384103948 0.19081104482479955 0.0782023356589016; 0.45100700641027447 0.27294379104242594 0.1169122829844832 0.18565419562870714 0.07449159587282632; 0.44956821031849664 0.2798541158760855 0.13604935406130786 0.19596795636983277 0.08540408166137294; 0.44709763389810786 0.28391260864935475 0.14866576610789486 0.20491008081890394 0.09544143857071365; 0.4533164835928668 0.29266267587822403 0.16812196587551267 0.21690870220547714 0.101056014251785; 0.45897770817747036 0.3011647369073369 0.16019029192152526 0.2193950426187976 0.09840193321472528; 0.4657092582835382 0.3089987858618528 0.1638743640742533 0.2206963160917651 0.09648478273682691; 0.4582596573554377 0.3043133496829057 0.16778537823850573 0.22016511633280844 0.10487384990161973; 0.45050647881213035 0.2961868726879902 0.15581309651608993 0.21240006803897168 0.09863188928609147; 0.4714394809928195 0.3255415982938248 0.1680366832437176 0.23719961380503293 0.11012215368942463; 0.46484686153146876 0.3258254450111737 0.1644591769315448 0.22814737109773728 0.10665779424107905; 0.46403969897439684 0.31858383985751076 0.15685271070302698 0.22065926967806318 0.10348336587267586; 0.4582421547064035 0.31308814384455047 0.1619360474419687 0.2186685433288153 0.09783952238096769; 0.46308465527604814 0.31413631636233774 0.15594443302727493 0.2196801726261565 0.09063572825538298; 0.4609968263078594 0.31118660965229394 0.15006722506981493 0.21394972894507955 0.0857100815895969; 0.457792017711708 0.31604468662472823 0.14305935797771932 0.21520769909158 0.08834458093434766; 0.4612190694439483 0.3244192885472954 0.1473309188896904 0.22395785701381882 0.09071051737141764; 0.4628408230009136 0.3224941481840277 0.1490668964238556 0.22133994243230598 0.09240631787357453; 0.4593071919014023 0.31921819366547777 0.1438093925000502 0.2168268811042005 0.09045128248832801; 0.4531253501836432 0.3084536533954407 0.13378008858214008 0.2082249990173097 0.07988418194812281; 0.4483382046273528 0.2972390326978894 0.12448404306848992 0.19701337683740583 0.07247484045753275; 0.4602600288431786 0.3019548096753861 0.1277455087477378 0.20005074933007022 0.07735452755315617; 0.47488547182408514 0.31822194166959966 0.15101513830617364 0.2168120685802671 0.09366968535600911; 0.4640713041331573 0.3027037352957856 0.1526046619240069 0.20607192664041304 0.0869370861408616; 0.45718710464685786 0.3015241003543958 0.16242109540491292 0.20803035973464792 0.08851223695735175; 0.43952905211806 0.28858957998043894 0.16322391274284512 0.19862147115830853 0.0909684410370194; 0.4429164932088828 0.2974342271652746 0.17203900947341277 0.20692585760882914 0.10587781951243108; 0.43836112268104366 0.29796615361904527 0.16024924653108086 0.20988465233271456 0.10600196498961788; 0.4413795288191971 0.2989987144449188 0.1466286169476125 0.21070168720583227 0.09710732268954549; 0.437548586987395 0.2941999919874536 0.1336048071175268 0.20387216354926513 0.09099590017529514; 0.4258506431285055 0.2839678108821763 0.13374242878671097 0.19557400997893085 0.09331247644926856; 0.4126763450386931 0.2712662839993202 0.1288290332493433 0.18984965548051255 0.0959414695684572; 0.39056251901648914 0.2555270601593942 0.12235867615439483 0.1759919504533836 0.09157347420727888; 0.41008130874842386 0.27085387383170845 0.12920379349309594 0.18696674249256678 0.09270058663587315; 0.41008745166945443 0.27858109811359977 0.14010996587052654 0.19834674828596932 0.09371696038564477; 0.40733214643230425 0.2719328317198303 0.14556527906238803 0.19178946263271987 0.08987137227074649; 0.4018915965289306 0.26601557637478085 0.14116799552106674 0.18705026166978217 0.0835122504736292; 0.406664740970169 0.2746024386503313 0.13638389483184668 0.18875473525001796 0.08235138665877245; 0.41607757562830805 0.28525471340958386 0.13505882322860602 0.19300591477453066 0.07873119273775786; 0.3999843828235845 0.27153915783837723 0.12186655342636779 0.18494642598390065 0.07317608259315467; 0.40685312210359414 0.26923414366305104 0.11807539862440646 0.18243202029037064 0.069901296791992; 0.40938965486556883 0.2739023510365504 0.11752601853646134 0.1872885094751325 0.07866933488652024; 0.39392244424081324 0.26184072643509054 0.10610508286267356 0.17388340963279458 0.06815321641707352; 0.4012144832265892 0.26481028437606924 0.1186297783319937 0.17036894665841462 0.06535516076321547; 0.42125693785766904 0.2799884958266611 0.12219247413196459 0.1856002267732954 0.06611948872037844; 0.4293886786907526 0.2871442125796791 0.12679077539855874 0.19287077339766312 0.06949686737400783; 0.43299153973337906 0.287663017635307 0.12211886230321436 0.19279563428781737 0.06745461161170398; 0.42486148897550025 0.2822868922748258 0.12202920910288262 0.19069274069326964 0.06670919039038017; 0.42702955463521897 0.28344457343404217 0.12653465089455737 0.19341270269122002 0.06155029070923483; 0.41879504091734265 0.2785883287206071 0.14137137744629774 0.19260210407707118 0.07697286413152818; 0.4034970098113583 0.26405213790057325 0.14544486156149222 0.18464120517518537 0.0789290916406298; 0.3939501280288351 0.2553219587955334 0.13796089957987082 0.1779256347047998 0.08002181710665895; 0.40203246551358324 0.2642155183437235 0.15214972194699297 0.187710824269272 0.08982885171465456; 0.4086841231791466 0.27299136861823137 0.15862730142806253 0.1992856583263215 0.0995240651726117; 0.39423030902610534 0.2600336030694813 0.13969643411902016 0.18301959802832102 0.09087976758952063; 0.39273618093861196 0.2604382420041538 0.14088501630518774 0.18612022475501613 0.09036418603082595; 0.3976615006266678 0.2596196599370938 0.13740799753502161 0.18291111708562147 0.08735145176426647; 0.38233205751885135 0.24521008968883368 0.12736870788443208 0.16968456841214952 0.07791723321855926; 0.3937335020407769 0.25646320653385807 0.12982974106397724 0.17783983796202704 0.07707973727369995; 0.39209808755753306 0.26109198866229766 0.12566962911150056 0.1852968186089481 0.08116550124712539; 0.38938606658647745 0.25698515485081286 0.14455677627294222 0.18062584995818814 0.0780498082600256; 0.39275593860205243 0.2613015211451309 0.13184417085861333 0.18145791411076134 0.07445750272569816; 0.38464999042555675 0.24825887674715177 0.11901002563647563 0.1709351149771543 0.06821992381451734; 0.3838069903262853 0.24606954987546648 0.10713015720337339 0.16885694424898876 0.06023098001609809; 0.39175407428808207 0.2534956271306741 0.1106083291776157 0.17185944565607272 0.05975365664347464; 0.3907223271470641 0.2584859021390333 0.12330346787032895 0.1800395776706788 0.062775202300425; 0.38956348913044736 0.2526178300686561 0.11979337967679829 0.17343978324555182 0.06493519411983142; 0.39503495945239864 0.2553740453964776 0.12267417162454868 0.17336142749804515 0.06176081581117352; 0.40600024901791254 0.25907192923595956 0.13096803784208888 0.1732225711442491 0.061370265499366444; 0.4029083847440389 0.2629227383770184 0.12496908593048568 0.17406361661731884 0.05829731286812872; 0.40575519199666243 0.26770172467530856 0.12175258716241452 0.17843940645360695 0.0603197433451736; 0.39340552088019737 0.25032928149462613 0.11616257206834105 0.16301013213319576 0.05457519385416699; 0.38982240674016866 0.2513489986305306 0.11021531970291731 0.16827012941776115 0.05332590058008347; 0.38255022022817925 0.2461326541379984 0.10862166763138292 0.16426230645607628 0.05479115080483368; 0.37581987622336066 0.2383362956345793 0.09926463032397842 0.16258291643008166 0.05501044705826133; 0.3683635051485341 0.23054830193525286 0.09921310933139496 0.15687624904429573 0.05323032272114825; 0.3583078547665629 0.22556188869480875 0.10683683527872223 0.1534640265934917 0.061541975893612474; 0.370147378392947 0.23972987070087265 0.10532753794086186 0.1634731947130563 0.05820935550970695; 0.37609974237118743 0.2454919432354265 0.09880993418846296 0.16806727816634193 0.05917749223027914; 0.3747016723301775 0.24109251119711347 0.11458742243412148 0.16516669527668013 0.06456029001406263; 0.3716234990236574 0.234428942744083 0.1070598080544711 0.16262619841876233 0.06650182571833477; 0.3805002076051564 0.2503883425745541 0.11391341803781516 0.1702696136536805 0.06524756747941292; 0.3686679742830539 0.24942583714748814 0.11147636567205052 0.16651374812146888 0.06039826655157499; 0.3503057115950222 0.23448065618535197 0.10694076881527789 0.1529340234615077 0.05830013446027511; 0.3506933254939743 0.23967278559891636 0.12010029268836886 0.1627141366177932 0.05577352174730678; 0.35092253907064025 0.23352692870210215 0.11932333062152792 0.15829899150324944 0.05658807975937191; 0.34949907599718905 0.23421049891241874 0.12122276326068822 0.16180154075776007 0.059643717093382384; 0.36068471621538434 0.24426593803031035 0.12543776551921038 0.1735498588526604 0.06309846608488887; 0.35952814301701574 0.24042776364217433 0.1301479154430935 0.17312550991728762 0.06366212670921587; 0.3742478996980364 0.2609202932368138 0.14286938914482666 0.19233947157823925 0.07304123047923487; 0.37725820425893264 0.26503652898871255 0.1491242993579298 0.19808327484102156 0.07424026581792387; 0.3608701350986592 0.24825631533784354 0.13698923676856278 0.18237549426532673 0.06883469554303767; 0.35549223802086766 0.24272614780841417 0.13300612342077828 0.17569411088925113 0.06223016496514227; 0.3668166786956553 0.2546208565535398 0.13449694630875855 0.1841897451075038 0.07014633032492754; 0.3642074180068782 0.2533300838949085 0.13350772593319155 0.18351260488765403 0.0669162375256376; 0.37239289382475305 0.257202102508688 0.13139978435754565 0.18517243198980463 0.0732341102778877; 0.3432972975522493 0.2281292190285874 0.11444652611708472 0.16309378957692441 0.06733417671084127; 0.35331580225230974 0.23673293869752507 0.11437100596980915 0.1708901279444985 0.06910959908294456; 0.3384296968269485 0.22311219379153904 0.10360826817358863 0.15890531218254506 0.06564683390798391; 0.3484255850067248 0.23213233196613833 0.11153218660517798 0.1668998805777545 0.06439390046908237; 0.36898436782761496 0.252650077294331 0.13847069254528893 0.18574026688705406 0.08031320284615975; 0.3780919821103738 0.2594915411083072 0.14508764891633522 0.1932176269274594 0.09153174528130707; 0.3650996435515345 0.24687463392481562 0.1439793771410714 0.18202430543753637 0.087687849351953; 0.3715013244813491 0.24549908617866323 0.12505058350401962 0.17769962082269297 0.07733315922752265; 0.36546290350483335 0.2381640766440414 0.12852018000473853 0.1724137477474412 0.07280842993009284; 0.348746827701938 0.22115702187050046 0.1112696986638727 0.15611933766977 0.06449341539719261; 0.35813552654601083 0.22948489789190818 0.11100896239226835 0.1622198212081274 0.06353523171288615; 0.35694979839974206 0.22867569688179437 0.09821533840851607 0.15868167781305953 0.06413549750123695; 0.3423395571188415 0.21676000943357424 0.09133804038728573 0.15074951661406075 0.06142889937022747; 0.3419692966998645 0.21649983219762386 0.08953890657874185 0.1506110317530482 0.05888810117252208; 0.3475600483942849 0.22147227579323245 0.0924650243437468 0.15581466551798576 0.05579628807669908; 0.3514022471848188 0.22678615553353465 0.09211763880778781 0.15822940406146044 0.054918363788652655; 0.3489084495976017 0.22818589232901126 0.09117952251139824 0.1590277410502624 0.052725901533308216; 0.3539025806486166 0.23156515079768014 0.11794192702534631 0.1652784084840927 0.05708909309239593; 0.3437916416406279 0.22091204776788959 0.11183542300035823 0.15514633342141418 0.056643825730334975; 0.3502069237613396 0.23093434655209547 0.11550546517984286 0.1659474455079596 0.05567269232722224; 0.3393068530387653 0.22456336505047614 0.10254393880380167 0.16267797114540422 0.055561694656627185; 0.3421808714252291 0.2337055781430573 0.10749474755774317 0.1735655020641429 0.05951199335242653; 0.3507857568726204 0.23344378900103338 0.09719787561377191 0.16891292539971214 0.056305310347758486; 0.33163487495305244 0.21777418241161162 0.08949106130783005 0.15632798270572934 0.051620002563065495; 0.32108363176442867 0.21067479241099402 0.08771982297328507 0.14931929207793646 0.04681327656429307; 0.3113148901069775 0.2028032152907566 0.08133443796656445 0.14125065731566566 0.044976484749883784; 0.3202359631224167 0.20830103032243377 0.08414371891039145 0.14675248148092762 0.05521640537116557; 0.32819593187679386 0.21632839459142783 0.08365038947834597 0.14921653951842892 0.06141949431446099; 0.344993772002137 0.22209957315891343 0.09179467840253533 0.14958264478555766 0.06771263916370793; 0.33677757532761593 0.21824919342493498 0.0876073400835929 0.1465121044596946 0.06026951609812199; 0.34848344327104963 0.2315973215063054 0.09406575049247246 0.15891257992433833 0.06916933815687512; 0.35828041435156566 0.2392802018133512 0.09673122503587325 0.1589902962926811 0.06626733788656883; 0.36363248348930916 0.2516023161576359 0.10386745781285539 0.16811318601638364 0.06736095864619965; 0.3558329150732314 0.2493150218380426 0.10543183505998432 0.16809671744084587 0.06290848076578899; 0.3556654418036107 0.24842396251781262 0.11707708156479502 0.16651562451820556 0.06767564481685101; 0.35714323834775 0.24376398521600945 0.1040503018408863 0.1665640729626098 0.06034363605530691; 0.35555533779619625 0.24305336632679925 0.09685916519640671 0.16571255886237454 0.05563379663587914; 0.3362411416606783 0.22685911125621022 0.10034848653458585 0.15501062960370884 0.0521781603067025; 0.34515894707335465 0.23872552805487968 0.1145912579948348 0.16793741000449264 0.053480599836024004; 0.33538210198317714 0.23161923284009822 0.10693386373954154 0.16315331230764074 0.060550735009123766; 0.326274530530252 0.22161604579032046 0.10745820842613488 0.1556894057608007 0.060991760084954806; 0.3360778998853985 0.2270197043080376 0.09415566527787614 0.15958059021761883 0.05309719757928682; 0.33485093208330663 0.2232796068397559 0.09526111019805088 0.15602527112905876 0.05055229200279103; 0.34011685444655254 0.22859908365467368 0.09147067086422454 0.16038413585142053 0.0474602134693097; 0.3637127009530245 0.24880746979124688 0.11470781935472496 0.18093157006037835 0.05477856112865058; 0.3517309568325185 0.23528492036348458 0.11028562127128608 0.16883762184963705 0.05401425968287347; 0.3391115003426475 0.21915318038372897 0.0998454773014813 0.1548093572591629 0.051681612218840586; 0.3494056291261993 0.2329630014603035 0.10355956622648473 0.16781051876822203 0.059954740532575976; 0.35535495097475706 0.24049588301219116 0.10651832039108464 0.17408704795582364 0.05821047235793982; 0.35843230577339696 0.24238621003180796 0.09615367399613531 0.1749667945555311 0.0626773035269349; 0.34207826687518733 0.23410881703496023 0.09570967651971556 0.16906736278942916 0.0683741720113253; 0.34284811483720123 0.23000469820022618 0.09777758616263371 0.1667498577389057 0.0655217902138309; 0.35965808643419883 0.24357578171348598 0.10475388147874436 0.17933739751600705 0.07008197794552455; 0.34868782292619815 0.23530636142139455 0.10351216328894108 0.17016103589553422 0.07322890820261486; 0.3524051450158395 0.2426574898596193 0.09797122852210212 0.17818318982139258 0.06716014032289702; 0.3509070390435249 0.24113347215140546 0.08646820382240619 0.1721897626258137 0.06291347635567442; 0.35318076324241876 0.24269069300242013 0.09486629284193679 0.17416815891561524 0.06302273337269032; 0.3334658480626545 0.22537425113636453 0.08050955818013798 0.1617366348480989 0.060155113551809025; 0.3441209405217331 0.23630838952794234 0.08826567966474255 0.1695759067754594 0.06330978076759468; 0.3496951508167395 0.24253721326458103 0.08136919206367461 0.17510351795519571 0.06143838873389157; 0.363477800102473 0.2528251690854044 0.09225724093903326 0.1863013824507807 0.06331433622743918; 0.3365419358503347 0.23045757875358355 0.08265199673405665 0.1673253358948401 0.05466773127481328; 0.36168952588172953 0.2531002618115369 0.09839700589363876 0.19050086987401416 0.0642503049172162; 0.357613369257706 0.24507784602969673 0.09314491792349103 0.17919152341195244 0.06011852666316024; 0.3430082674276491 0.22833057449602912 0.0843351290132847 0.16060005366331973 0.054871008154373103; 0.3429089089593617 0.22348182166690692 0.07869861517399522 0.1559717763624719 0.05005378565221686; 0.3251995484321378 0.210883264860114 0.07676068291306475 0.14841328236755777 0.047202743667599835; 0.33309858761541544 0.2189775567218467 0.0797202391047476 0.15510723927257097 0.047353778096626026; 0.31242978352159256 0.20249445525525447 0.08498315434608444 0.14329293520162611 0.048271769334943954; 0.317185996197462 0.20627735088442511 0.09434863564136492 0.14862395942934442 0.05521746550009399; 0.3116909847440719 0.2003692470405479 0.08973489413072958 0.1451389322338747 0.055826454701071976; 0.3098044980194091 0.20291487335475125 0.08774655528394615 0.1503227456139125 0.05410104490681171; 0.3122344186803436 0.20593393313337835 0.0918783592583993 0.15084426333320916 0.05043546306978607; 0.3104849355141906 0.20561776830712536 0.08588722724932502 0.14940813366423275 0.049964814715710834; 0.31713094486559135 0.2029265922225283 0.08508440110459382 0.14441065934380076 0.04743785060097977; 0.30962443291159236 0.1998507091932906 0.0912572637468533 0.14459697959486786 0.04609628038923108; 0.2984906907003066 0.18725729958481896 0.07874462889790187 0.13477990375092938 0.03976147244479389; 0.28771660825577905 0.18091158748680203 0.07891938199329099 0.13037803150122415 0.04524410959169174; 0.2914012221572203 0.18799002314419627 0.08203480628909843 0.1391471276832028 0.050790201692461207; 0.28265036031225543 0.1812933015410986 0.07688583920623603 0.13183575323441854 0.04562664464607178; 0.30528296339209254 0.19833478948155134 0.08140762837907269 0.14426201741869632 0.04808464768921804; 0.3143302127337088 0.20743721024735046 0.08346167905871546 0.15392175742765574 0.05828526416139182; 0.3404361307315532 0.22965062893663463 0.09448693655923585 0.1714209978086178 0.061360217521320794; 0.33602985737264185 0.22475520461586806 0.09095987648165688 0.16516066704610385 0.06343720397530478; 0.34944338200521496 0.23424522828887062 0.10685032284574877 0.17363280049498397 0.06633950256251081; 0.347171162351227 0.22631733617647615 0.10300188701404867 0.16546200507112754 0.06173908821100223; 0.3434527733200838 0.22369608979594013 0.10893184694491813 0.16424254114014636 0.0620507785586852; 0.3485813850779573 0.2333303090029661 0.09900316747302206 0.17282951302991495 0.05955120783315804; 0.34131241159591985 0.22918400733420882 0.09600062193293882 0.1688306812657212 0.06373088994635508; 0.32936864151123296 0.21962417816122082 0.0884311339999796 0.15771858219013968 0.0615674533070196; 0.348019938099886 0.22898451809088158 0.09460615897143371 0.16342662730778346 0.07300720782050048; 0.3434110128311356 0.2248353258689226 0.08954858608217627 0.15798621244402797 0.09183313585097436; 0.32736015863641427 0.20999202795187483 0.08307324212528538 0.14717326903082587 0.13502609043737127; 0.3235457940691656 0.20730178588517387 0.08268981317072926 0.14648704106599217 0.15787631916538775; 0.3286029480929332 0.2120688868275315 0.0863446167261586 0.15131947298836806 0.15439216115105867; 0.3349578744598355 0.22129502993512395 0.10366363693485144 0.1632329366603859 0.1486290609282551; 0.33659616640632356 0.22174391827335552 0.11174108580119993 0.160934680064469 0.12682289107182007; 0.3345989388738076 0.2221940839795319 0.1035345101981766 0.1658721155802007 0.11636890797645554; 0.34269619206698737 0.23309950308068972 0.11743448810811098 0.17999552185373272 0.10951695256496036; 0.37332858022143045 0.26875970781695346 0.11957112063594863 0.20482177134384125 0.10385791987629385; 0.3529047956155904 0.25091534770211776 0.10143593264324034 0.18630978193703818 0.0925329642927778; 0.35810007970231117 0.2539643340641753 0.1209725434597537 0.18659121177056257 0.08978944112349607; 0.3483416145698018 0.24252643830255638 0.11431661655634284 0.17864368563063004 0.0781479643940056; 0.32474223122245366 0.2204323144489604 0.09603241411947919 0.15942553047471889 0.06885036440961557; 0.31927402889924283 0.2121438558287682 0.08652827925963173 0.15336725107140262 0.06130368177909055; 0.32254500847019385 0.21446664237080112 0.08355831086622056 0.15739585750346913 0.06020021668925602; 0.3289605987942825 0.22072703522919096 0.09196537816513678 0.1645313077612363 0.05698169952118173; 0.3321423958044537 0.22202407226942758 0.08118819437614362 0.1644735027109498 0.058150728030870555; 0.33519607029766146 0.22384642387217507 0.08927258395903334 0.16666686743536901 0.06317408441215372; 0.3246031641356969 0.21217929978995503 0.08627912337583721 0.15493041741879235 0.05954248430299454; 0.3117896925920505 0.20482423929237512 0.10092674442134236 0.1529164709093686 0.06141137160434479; 0.2990143367858139 0.19586080930919 0.09208717617791443 0.1452356520249459 0.05583062556444927; 0.28733328832875943 0.18409261303973634 0.07843034045121311 0.1339187099897077 0.04733939597653805; 0.2876113661423624 0.17980287530289044 0.07645314396398258 0.13016511047786158 0.0459142948559718; 0.29180554813506604 0.18410321123016635 0.07822622675480041 0.13350899453882917 0.04529760681563987; 0.3062428575067711 0.20333553390989906 0.07887658581162765 0.15201156982520853 0.05081710440297424; 0.30461744398347473 0.2019189171973086 0.0825403415562731 0.1502895833948424 0.053567356148397915; 0.3176779344119385 0.2137198108818703 0.09371447331921434 0.15821357026888294 0.055858667714624395; 0.3261809145957434 0.21665099528523868 0.09228265696538429 0.15744819307480942 0.05204512086369895; 0.32038197680713365 0.20652933929040104 0.08088644848285469 0.14885069729212674 0.04530160576588554; 0.32373020064355235 0.20823939552842832 0.08287309164618135 0.15056679786303642 0.04345277160792861; 0.32334332475281796 0.20677877097081548 0.08414749546698476 0.1481446237648249 0.04345564040851048; 0.32181339509659646 0.20083242856463912 0.07453180124443169 0.14013110439258578 0.04131501957425635; 0.3120840950598211 0.19456753892104725 0.07562472985252854 0.1367572275024872 0.03958117773850092; 0.29949402322688823 0.18851326415857395 0.06822637272727582 0.1342544338879761 0.0404892586030112; 0.28686153201515774 0.17833873637454287 0.06139713443598821 0.1264390369675777 0.037284516084793905; 0.2957019929747208 0.18572490817655385 0.0657890164238745 0.1332057820099371 0.05328443967390354; 0.2884807804950415 0.1785140526799302 0.06787612326006365 0.12622755120895524 0.05175651643147703; 0.28128353315419663 0.17219389716847266 0.06719922005780754 0.12409310122889057 0.049894105909034696; 0.26988268639903634 0.16513469310652037 0.0655279547842202 0.11880577419647992 0.04561700022639043; 0.28067437407383417 0.17124313904484764 0.0719069791533039 0.12079226723869181 0.04480146097279554; 0.29949096915729123 0.18575386141650402 0.07391584437668211 0.13238433402029304 0.04453912334352307; 0.2968923713970763 0.1871012821587922 0.08753999290132432 0.13504949828980467 0.06118716563152927; 0.30305140345959525 0.1870638400151731 0.08196324307532238 0.13365472452639024 0.06810245128764833; 0.30076493525241743 0.1851645177471162 0.07556255319763126 0.13179638214348538 0.06673022528325816; 0.2808218733766471 0.17085599230667123 0.07162326253691437 0.12323378753613459 0.05742102735607068; 0.2960512329180077 0.18011324764839942 0.07541937273533442 0.13275804803332508 0.05578087914680036; 0.2938225797048438 0.17788096894067235 0.0756321511013611 0.1282629554316268 0.04954180599705054; 0.30424626519133474 0.18760784867796665 0.09176060250149598 0.1374183026826275 0.0635337092992121; 0.3111761538175728 0.19491368356063657 0.09281118713415806 0.143579541872016 0.06568396159143877; 0.31111771090729917 0.19924307622682805 0.09495228183346704 0.1485047513088158 0.06897967809940682; 0.30738274036966867 0.1952499211483936 0.08530129290284885 0.1462828923337119 0.06523483871027078; 0.32535960697430855 0.2090806294007095 0.09913922088672457 0.16099986704766409 0.07073262833439703; 0.31475485701003464 0.2035166713414981 0.08681360994640777 0.15582693435811723 0.06361165967888352; 0.32621921768696144 0.2111401303862249 0.08562219134858282 0.1582689886733987 0.06310709527974698; 0.3132249786131464 0.20443100088872235 0.08312328451387907 0.1551359538590986 0.059171115303797504; 0.3047466575044698 0.1993133185628074 0.07665174911231061 0.15069487546730664 0.05970566367686826; 0.2882708101620918 0.18365687297368188 0.07906600751328675 0.13624240640678906 0.05461453439260354; 0.2886274170200543 0.1850858612186443 0.07922027790823148 0.1357596203397028 0.05128202868672077; 0.2840346822198642 0.1815799997907266 0.08599342532379282 0.13248592195592818 0.053703369960561305; 0.2906904442355166 0.1863550127872932 0.08650489550767622 0.13523508868759868 0.06082881571084253; 0.2901878713166817 0.18669060717655087 0.08655638120125358 0.134205549058485 0.06958487595105164; 0.29265925753880373 0.1857820429454872 0.0938462798519979 0.13090169656051634 0.06651427643485064; 0.29728511348381703 0.18780971889103482 0.09124855675093729 0.13502351524649808 0.06548012085348125; 0.2997719615699058 0.19752091625853402 0.102976482930123 0.14501394893502195 0.06332589939307973; 0.2740646278859143 0.18289882309853253 0.08604905278272565 0.1347820922992627 0.06321838402805173; 0.2717250387669376 0.17821750933026645 0.08465641207128474 0.130273915550073 0.06877005173013563; 0.2773676833153384 0.1834815483816097 0.08632776015305288 0.13381181039091747 0.06947700439489647; 0.2746404366207613 0.1832939180952414 0.08448113251371199 0.13683941763779958 0.06608960511165272; 0.2816677118549739 0.1883953019557082 0.08530699857984396 0.14018722913377635 0.062157593026776405; 0.2790676375397042 0.18175969358902638 0.08323111106089284 0.13459435784191412 0.05321381748618229; 0.28692823808733586 0.1866112417906242 0.08289533928339902 0.13818820960021433 0.05347416136385238; 0.2827015233941393 0.18090755875346798 0.08048749923948625 0.1318071545894656 0.05086579811550169; 0.29077281458437576 0.18203839667986027 0.08589286971286281 0.13388200594867972 0.04863217014652084; 0.2726718904833804 0.1699884951778268 0.08094137355244432 0.12384703104802534 0.04370563334092769; 0.2701447345623025 0.167072463684719 0.0736266263390086 0.12432203964478625 0.045041191177489545; 0.2608249485737998 0.16063469342664177 0.06776022617534812 0.11791940153508863 0.04216226731989557; 0.2552226543622747 0.15677099877417322 0.06683102611316058 0.11839950180744713 0.04374576346281191; 0.25910714151044967 0.16492841405725667 0.0700427024651592 0.12492276506976752 0.050465552399182476; 0.26542804743115334 0.17483866225128322 0.07381264798553984 0.1339590680786488 0.062326209457416654; 0.26515605135968706 0.17321807452396512 0.0740686739103969 0.13035503186293582 0.0627704931987916; 0.2786977516350061 0.1849185759493189 0.0681223385228297 0.13913180953270704 0.06104111959088601; 0.2921549917647767 0.19395037072249072 0.06395179779875922 0.14750434677606034 0.05343746363261348; 0.2842343641431751 0.18514540852982056 0.05845604689159908 0.13563806739096013 0.04893646811754708; 0.2780943308760025 0.18402727891507348 0.05693241835625106 0.13638749561027025 0.05036638866115574; 0.29868328130160154 0.2055992857575623 0.06223660463882394 0.15646500461352136 0.05386636408367923; 0.29790058379105233 0.2042689562606977 0.06623797370825535 0.15778596955976698 0.051690713333679604; 0.2906727524179737 0.1983008278026713 0.0706136515047894 0.1512811025654619 0.045505994795833726; 0.2965102518859323 0.201746884394847 0.08404168707583318 0.15729065761370223 0.04753309924528972; 0.2777403940965983 0.1850586769256295 0.07266403240922269 0.14143478542886387 0.04309420226813138; 0.2937507132856252 0.18686696388509283 0.0746757691340699 0.13991420901077756 0.04186603601813937; 0.2745471735929014 0.17264308381626137 0.07982673239605062 0.12998308240380102 0.04003021186423798; 0.2674407682923127 0.16359438279111485 0.07140418383992857 0.12023416309758993 0.03448385667220751; 0.25262648042898567 0.15341749561897355 0.06987197145634609 0.1130623486574886 0.03807857495678266; 0.2552451982248719 0.15424533604042878 0.061175440309951444 0.11229128574819547 0.033797657511693634; 0.24972260647208655 0.14991447960104268 0.06647671823383151 0.10988744048667894 0.03677149297560246; 0.25388609690023395 0.1512123217961448 0.06986352405691766 0.10863873569880284 0.0346887625298102; 0.24865903912030007 0.14748867021252773 0.0654506905018856 0.10228647159508353 0.031109655388490306; 0.2577178435170042 0.15283575786153525 0.06587286427732864 0.10316201342718986 0.02938944333854989; 0.24750422788805865 0.14696009711821914 0.06418945747706539 0.10279320066036533 0.030402163786202082; 0.26693745933490676 0.1595126738659544 0.06757173028066354 0.1129101416258951 0.03398868650000048; 0.27819568103565917 0.1730955879300438 0.08384512433588184 0.12720003233662763 0.04574435967048607; 0.2617833301306895 0.16291458480831802 0.07643019090437633 0.12203883434384281 0.04485257431142013; 0.2630771982575362 0.1659290369214759 0.07135364978785311 0.12320550425886484 0.04779596921223386; 0.26496552132804435 0.16088137534158595 0.07259326731582479 0.11875947629641988 0.048882573218488566; 0.26406260294309647 0.16070169911302856 0.06785294954315818 0.11942688725576002 0.04863160500633229; 0.2553182668494494 0.15284617060834355 0.06093480498064356 0.11291136425483383 0.04818127621974555; 0.24452810402769337 0.14437366278500705 0.06275388050451912 0.10606888994970448 0.04658964902970002; 0.24311140510287674 0.14770855606819272 0.06012267851531536 0.11004169237930399 0.051876448637746216; 0.2359887268769486 0.14413539052983187 0.05938718951702142 0.10717075280204472 0.04624796515921946; 0.24822967502496587 0.15722181881252975 0.05755730136799832 0.11883266835892245 0.046051057030520405; 0.2609437883140401 0.1626031864466989 0.06333921533479706 0.1220464125830654 0.0424995768614702; 0.2564003402186835 0.1591760829117079 0.06394158944808973 0.12087023381858855 0.04068495495502889; 0.26304549647914605 0.15763371408193744 0.06033854624886141 0.11595028737759423 0.03648277129439306; 0.2816083603981911 0.1688426313416913 0.06048285790291488 0.12280364711742267 0.03716714709566269; 0.2832276184466504 0.16975943367614388 0.07011936319277334 0.1255678922308339 0.038653204079995424; 0.28522758158898537 0.18188560601817796 0.07268064538562813 0.13731207969767675 0.0463873474689562; 0.27671523668651726 0.17867162105836254 0.06847690399427826 0.13551191606507956 0.05216778895395906; 0.286605443781892 0.18327524087745176 0.07212676986805291 0.1400471329163413 0.058829560030602704; 0.26590970156691834 0.16782648819222631 0.06607161569397998 0.12896124120322075 0.05335803113309804; 0.2552319943754066 0.1582307767473426 0.060130209587425806 0.11742670264456437 0.04704488603316358; 0.24750952063784515 0.15313694986524315 0.05786521056287354 0.11319015613487377 0.04407229329580157; 0.2516883106135171 0.15723319938041475 0.05835843960637145 0.11722284012072097 0.047853264653158895; 0.23965187200727792 0.1447586240590231 0.05494898810143704 0.10505626064962396 0.0423900978066307; 0.2603698240027645 0.15878161269192825 0.05165337377115436 0.114869532683899 0.049870138569496604; 0.2472655845726187 0.15035990955642803 0.04873922300993878 0.10797711129936377 0.05956124629880788; 0.231009813987784 0.1385053452429131 0.04796883554386678 0.09909743848206838 0.060102881670441644; 0.22706628965820663 0.1398876533172095 0.05010331718029644 0.10349313791801326 0.062464168513175974; 0.23836658300944802 0.15289182068996143 0.05492810247661325 0.11709948381749624 0.06175986173300515; 0.24969083787591168 0.15971643509143602 0.06258824686862352 0.12149077455971903 0.06581470116018112; 0.2532462117798401 0.16420609082121856 0.06950334783917525 0.12726258775213772 0.06186254417132422; 0.2475582907777844 0.15493250449768073 0.06960110774855502 0.12050491355355114 0.05559334793373811; 0.25907185873840793 0.16854233590977483 0.07457943289455324 0.1265097123980167 0.05631354586231603; 0.27237117450598514 0.17694551883711093 0.08361972593447803 0.13230512838360806 0.05358403880157386; 0.2782950652532866 0.18331514607726473 0.08516490388457965 0.13955969950196853 0.05625926968461922; 0.28781156165544913 0.19056301363991845 0.08725174310640486 0.14830917291353313 0.06802641663556616; 0.2797273540349382 0.18119609791983884 0.07443489118684127 0.13916885095842813 0.056705297290129034; 0.2821953887821498 0.18113011172572552 0.07372427868261969 0.13753107478625087 0.05380009438303516; 0.27607092818270224 0.17247715931065702 0.06398079765272169 0.12958789102559493 0.04733371322915877; 0.26745752839764037 0.16490183147532006 0.0635338756237986 0.12551771736006107 0.04938635496748229; 0.28055915712134105 0.17397225298676697 0.06704626045978564 0.13202876953967543 0.05664684389792077; 0.2786656417752589 0.16965170819118663 0.06560805588846602 0.1284673480883291 0.05869896671980374; 0.27275390214167317 0.17027308240377936 0.07618250220922787 0.13182854701638624 0.06893011897253794; 0.26648471980446403 0.16779811537141825 0.07768258219884362 0.13325930575180375 0.06674388548292956; 0.27047756099028447 0.17322680537601493 0.0942214559787633 0.13684670181789654 0.06804406146652095; 0.26563185281215557 0.17115330842892473 0.08253976851893442 0.13119349421436516 0.05686588113861556; 0.2783864484362479 0.18050751803525403 0.09513919770870985 0.13650731576581737 0.05552648673738857; 0.2665345824664971 0.17043569956785928 0.08911842680100109 0.12983624653498285 0.04911887209841267; 0.2831104164843671 0.18169836024098787 0.0875992165098469 0.13772279037221236 0.04814965674264157; 0.2740427426914304 0.17273293490928962 0.08722122350056016 0.13156848262297283 0.04963901807056208; 0.26875771462280984 0.17080553218303168 0.08891280860677594 0.13255461045541103 0.05150322676051727; 0.281646042103445 0.18715260302685138 0.0931027138906736 0.146127686806025 0.054978949311169555; 0.2794436923939987 0.1870495239946241 0.09122248130464702 0.14543080998063238 0.06002179780228342; 0.26855705676706665 0.17674538573050458 0.08375844915647626 0.13731630383014798 0.057725305595981324; 0.25035166440989204 0.16187300894994702 0.08026397375217532 0.12476300339365101 0.05353961879133165; 0.2521758413202415 0.16552521279922458 0.07808859018843536 0.12613986345501021 0.057650324655524735; 0.27146262811715205 0.17869087748902107 0.07508422081360153 0.13263383438087523 0.05338897313908883; 0.2712134729790274 0.1797563796693251 0.07731703535468523 0.13307795468884326 0.051757252514252255; 0.27393786398312125 0.17872048242522598 0.0732350711286159 0.13293855026497536 0.05362936237445608; 0.2716776771365855 0.17024996637211895 0.0755362815070225 0.1261262248765158 0.05405357359044659; 0.279331949791849 0.17286549018944625 0.07795734605455981 0.12916240003194232 0.05740138344520654; 0.26425030922217396 0.16434460188647368 0.06934088911624421 0.12268144115993038 0.051012003541424475; 0.26225419120250726 0.16494120403687365 0.07040095832754509 0.12579595625550472 0.04780636856590478; 0.258470217595566 0.15953986143716342 0.07087577537146676 0.1217423331153466 0.05259664012698149; 0.2558181039174944 0.15199846909958656 0.07413478219864741 0.11393268020248999 0.0463695927010601; 0.23871181421920057 0.1408122252346558 0.07119154204414667 0.10642015327053539 0.04269260245932144; 0.23349600941693305 0.13879800108444554 0.06877746523011828 0.10641513577331918 0.04109073269067607; 0.2447731785834274 0.14958204839525113 0.08336879086962624 0.11268439440909876 0.04596467187164943; 0.24282596948627166 0.15253653040645512 0.08547778693812119 0.11499970345881663 0.04908492238449033; 0.24225724592116302 0.15224587648008658 0.09358116303266706 0.1164870212609536 0.05740374929608485; 0.24630768978044848 0.14954117321089422 0.08105401522423127 0.1111640264697843 0.05114089956404035; 0.25461234755075346 0.15437230474245955 0.08620808284684259 0.11381966661278194 0.04823555855370573; 0.2434412557423621 0.14926238959226934 0.07761072748863092 0.11072128149560122 0.043045578616197996; 0.24420840589527365 0.15676331106975816 0.07482549853295796 0.12127294447176479 0.044683947487541904; 0.250548460470232 0.1580688920351278 0.063546642867094 0.1205534626535799 0.040112976937587155; 0.2657728619468948 0.1616938653971681 0.06677921728878475 0.11923515415129868 0.038785882311340246; 0.2720835250292413 0.17057274130073619 0.07114303453039532 0.1310927181715791 0.03732793705048249; 0.2525428775290007 0.157311971760491 0.06484400902804856 0.12203113758762874 0.0352858388533758; 0.2587867453367992 0.16273786089952744 0.07097734252307514 0.12966758330027417 0.03790474010392562; 0.27480098602545133 0.18942918747374182 0.07314886094883044 0.1502968396294924 0.04520330934035409; 0.2975858926564206 0.2014182547307711 0.0768704111715552 0.16069183254629868 0.04853620962943735; 0.2838044428658286 0.18855212347322314 0.08181539140863392 0.14945956869435706 0.05157012809631111; 0.2889182836875756 0.19361743105740237 0.08880507916389443 0.15555001639137583 0.04974701211306955; 0.2878733194721094 0.19129604517055263 0.08275136551402838 0.1543642150784327 0.051101679000882354; 0.27896802062609605 0.18484754895077316 0.08177563111895586 0.1482739715715085 0.05331870244433724; 0.2919858688896403 0.20070430068100426 0.09530624398322315 0.16160318306603708 0.05945219309322233; 0.28289138037248496 0.1925508811308935 0.08398266677046944 0.15126105140859825 0.06549219954961297; 0.275103872086875 0.17850313359371778 0.07322391033359471 0.13865595254274163 0.058739722372720696; 0.2651276211470543 0.16403935868638322 0.0718920670762706 0.12623839482046725 0.05294311280678118; 0.262519377114787 0.15998781338610304 0.06771396490455057 0.12277169697982122 0.0522808019171588; 0.2805468759079093 0.1701426703951999 0.07637777789449998 0.12934433955750504 0.04945771590673386; 0.2688668714872451 0.16387278828797694 0.0679245937984491 0.12010274311941178 0.04537447027010488; 0.2484589673607708 0.14907324656866358 0.0592766342607184 0.11059881632360866 0.03919428528909101; 0.25064005315535554 0.1432625038029541 0.05005100063360086 0.10406104830768148 0.040099741054091566; 0.2484536467809144 0.1453834460259906 0.055874369079878736 0.10681999163124116 0.04650583349268731; 0.24147004773765113 0.14622254261028222 0.051523569949476565 0.10863359172179819 0.04918793699225661; 0.2623813759529535 0.16104280025682013 0.0600941896263827 0.1240589372240267 0.045688739556716894; 0.2584841796750978 0.15957566059367784 0.05669554008635434 0.12181239242734605 0.04371110837749403; 0.2533787388797724 0.1556687957583819 0.058973682392379066 0.11901041599418398 0.041342497794562665; 0.25695124063461017 0.15782212070933616 0.05680547900497152 0.11978464509889027 0.0421880744327975; 0.2593146367356697 0.15762423556893376 0.05340593579410898 0.11841786899840467 0.04244382678905111; 0.2635035537469799 0.15790596172689841 0.04578687802850714 0.11566040564517684 0.039482542495441295; 0.24988470258620699 0.1463456506767229 0.04594430620193092 0.10733147481235271 0.035017049085507276; 0.2779399337951924 0.1694048508197749 0.06004178907251046 0.12672480161311153 0.044854173180587674; 0.28220457097566803 0.17764800303703027 0.060246691193387394 0.1365222749338303 0.04825544932852394; 0.2812612792704636 0.18232128531555714 0.05956820554431716 0.14361489154702456 0.045225045219025664; 0.2523941956642576 0.15855049449857378 0.05286810262021573 0.12355966761951473 0.04497406821247868; 0.27704948486354414 0.18104553309008523 0.07381483088348031 0.14561435497001668 0.052024979915594516; 0.27615686894628577 0.17414058813989197 0.07080008771350955 0.13805786304629533 0.04717572206864791; 0.26663454187848706 0.16830224748086958 0.06674850159947852 0.1332772535718019 0.04575000469573368; 0.2617207522228443 0.164613483990288 0.06145585615686401 0.12905396174482783 0.04140576943010513; 0.2582660867798395 0.1604921777209093 0.05279178513985336 0.12278535684817855 0.036433368840817; 0.2514870189847999 0.15392705175562302 0.05094364856800604 0.11555105672974447 0.03695767589926989; 0.26511239594002195 0.1612782130502351 0.04999840716617241 0.11777899743476757 0.032438355744542846; 0.2701639261705051 0.1638787825793177 0.05002871968425858 0.1218344684947272 0.030983603197862444; 0.2677781185994442 0.16486201802016498 0.053748553042233374 0.12549181910425344 0.04343850509208817; 0.259679926553559 0.16440459187127113 0.05389664201507599 0.12824191953396732 0.046113975859740405; 0.2652828857256505 0.16801682587700653 0.05555683426912332 0.13009831353549905 0.048349751197941326; 0.2704497408829954 0.1723481841980423 0.06710342508837147 0.13330124055961567 0.05400347116680719; 0.2719631419152281 0.1677836579560443 0.06725111011492858 0.1276520737856213 0.05053572999907953; 0.28409724240066697 0.18094577411645285 0.07032983127298077 0.14176425825354128 0.06336045183716951; 0.2721234852438139 0.1764677685088605 0.07500414350082175 0.13909271749493812 0.06559404963635396; 0.2615807767204418 0.16794635924392465 0.06858378190556921 0.13081971867988376 0.06211131624883803; 0.24525071406300655 0.1553220421885929 0.0654149830938161 0.12071699302681183 0.06357452869420363; 0.26226936359354486 0.17023605472369843 0.06935265456444267 0.13462568542391376 0.0751440349221636; 0.2624349481197089 0.16761459403454348 0.06889284537081912 0.13067863510871183 0.07280184262994202; 0.25891456892743825 0.16556288296555746 0.07604930508808291 0.12956134678383074 0.06666393525603034; 0.2557712327691326 0.16099546845416443 0.06555481035948592 0.12449891329971474 0.0616542007303446; 0.25300528556127627 0.15890759226211085 0.05992503214431443 0.11983260978196082 0.05838818918873544; 0.2594949996472937 0.1686920463762933 0.06917217025003941 0.13077606633451794 0.059604499309934576; 0.26473332810414174 0.17258210299191903 0.07367011178606439 0.13368757367251088 0.058845741158467454; 0.2667698611260441 0.17457353923939092 0.07432768062014332 0.13887479245756285 0.06120000738361829; 0.25753539001472686 0.17081340733545958 0.08048891079631607 0.1371937639720775 0.07473264899618906; 0.254630738063875 0.16691016819777438 0.07093986339137681 0.13498138067782223 0.07130818280988918; 0.25502948845563184 0.16817038986446342 0.06922458284509761 0.13650658867883922 0.07455947419733991; 0.24929949947307786 0.16036539163877075 0.07638202298412786 0.1313591983288784 0.06871728287721626; 0.2535519505191666 0.165277725551045 0.0791324143706168 0.13562163800956878 0.06920769859619898; 0.25275140242964605 0.16938594467919355 0.08742007534491263 0.1331420816259549 0.06326297039205203; 0.26248785843205913 0.17574208766207125 0.09043988671531075 0.14218717334882147 0.06128925399513538; 0.2729029595037497 0.17888315451133271 0.0822646565169477 0.14335348521245103 0.05502236252750155; 0.2772217225376922 0.17909680054178254 0.07634675751569935 0.14081226340589986 0.056697466895780535; 0.2719320401624169 0.17593078709117901 0.07893255253984982 0.13901940923260106 0.05015348085824774; 0.2787303602755329 0.17785737829583748 0.07052910770260853 0.1365410402721282 0.04508968667438925; 0.2608718853044717 0.16634497477354895 0.059934303723045694 0.1309836742525193 0.04225385704140902; 0.2573266729393171 0.16439491855098637 0.06044312760215482 0.1307843307451322 0.04364408219656182; 0.2373993420345439 0.1496109066167977 0.05502186945066039 0.12040375608570691 0.042561775762246706; 0.24127210567338098 0.15620160681084844 0.06811100875127461 0.12710363021188828 0.043851435735548866; 0.2563804736927575 0.16534107492030503 0.07567986009349939 0.13372081200833202 0.04402220665790664; 0.25943134237888865 0.16506315720606518 0.06372068600122545 0.13283171399875546 0.043764443303172; 0.256574790752438 0.16175745091858446 0.06538133145383528 0.1298889017656967 0.040426664932588105; 0.2542339561990955 0.16512651472904633 0.07548777616827909 0.1324423211062372 0.046055711018259816; 0.2471239804118521 0.162726680275745 0.07993528282093385 0.12951401877358915 0.04698528733429551; 0.23785540869948443 0.14820514656062667 0.07203119425334437 0.11626586224997332 0.040947808789827345; 0.23648065953347824 0.14343337147995427 0.07071622751838288 0.11261109039278261 0.03938423089593086; 0.23951406382635232 0.14450929307591592 0.062434726671865164 0.11292477071357912 0.038810091405387194; 0.22683288437616822 0.13925266558847169 0.06081062875508514 0.10968235528527218 0.03649082916619418; 0.22183080838117597 0.13793507750766545 0.0677072908267915 0.11147850768612637 0.03931837489320467; 0.21807981491878506 0.13344559499372696 0.05966464761678694 0.10448429150856983 0.035083054806698405; 0.21455595660841367 0.1313319374422205 0.05415596109655951 0.10430080275517664 0.03303534892174327; 0.23465334787874143 0.14700859938462357 0.054621970242480083 0.11908017262444466 0.033828060185692496; 0.22735348176883635 0.14359162274519427 0.04713155028122238 0.11556384247243857 0.03147700879437271; 0.2327103303426661 0.14119691768105685 0.04781234992065089 0.11043395921945935 0.030915339169601944; 0.24193403613997763 0.14243389661165762 0.04139774725848879 0.11057089329052262 0.031157893441280005; 0.23933202717648558 0.14098784621598473 0.053836091347650245 0.10888578790655369 0.03221219952079477; 0.23519045367993205 0.13606850591136735 0.05857534775186821 0.10559336283390232 0.030213789543889542; 0.2298949023497684 0.13158210644589838 0.05071667152384317 0.09886363298562771 0.028635710473960702; 0.21951687915425167 0.12819373531712672 0.048108659229591656 0.09676820606682783 0.029516526308541347; 0.23418582545360456 0.13541728197394673 0.056351747744810714 0.10508545792654422 0.03293257489552883; 0.22690449310652838 0.1290571699647813 0.05697952166877757 0.09861099069559787 0.035877649513886674; 0.2342398913964623 0.13520805320014231 0.05923968965357598 0.10430952386255433 0.03494346985956534; 0.25143532174944827 0.14829111521140476 0.05852799819545791 0.11773081303592817 0.03461439092747771; 0.25781506075954397 0.15318048337853543 0.0633072238694576 0.11910330349966919 0.037943586894213385; 0.25377461134986845 0.15362613471155637 0.058463679276382734 0.11760137255799799 0.034018925727080686; 0.25341692423500034 0.15152285553459544 0.06352096022961601 0.11589368304262185 0.03749439743214558; 0.24169390086871317 0.1462816769476272 0.05270513385473144 0.11218688981254597 0.03384459554297694; 0.2400871082905287 0.13896127687657175 0.05097571355055532 0.1045305220009462 0.031977475993974755; 0.2299053978731914 0.13034773237915276 0.049050301050748514 0.09826911192906507 0.02840840250304838; 0.2284337798206555 0.13230692142177772 0.04281157681195425 0.10050469449577815 0.026938896939567726; 0.23249650851476567 0.1372396403068634 0.04456496505020847 0.10634021013115316 0.02485360565516313; 0.2234503843831092 0.13325667210533873 0.043823206320037764 0.10556714027432179 0.0286966680505511; 0.22674685962574243 0.13477569383871282 0.03927825427622026 0.10612028073714237 0.02644993193098997; 0.2249648173457508 0.13425007710847636 0.053757638029817145 0.10748210236585984 0.025608167168689525; 0.2282953987364868 0.13428448637321297 0.050837010377695876 0.1059376542580672 0.02277975520119489; 0.22211755055943327 0.13079799513017895 0.05116797257189013 0.10157137521605078 0.02120572526008225; 0.22055909326679865 0.13035962422685435 0.055479735284837545 0.09971319264968541 0.025739821881058507; 0.21927111082082876 0.13278484992183534 0.05676392701251702 0.10063259851376459 0.028262487274410483; 0.22539219445233255 0.1369879714806659 0.0511962257532946 0.10474186381848849 0.031044226614238543; 0.21728115825847555 0.1275927412239538 0.04631033899058276 0.0967124670040782 0.03487852626252311; 0.2123991513172449 0.12651047907096755 0.048304941399251414 0.09783042723275628 0.0341484288927566; 0.20602406572657117 0.11994913112578878 0.04058072353619734 0.09286556793719457 0.029874784556063093; 0.23196734795059593 0.13561088058517845 0.037571086070683796 0.10594450556015911 0.030871017769600613; 0.2221380764968064 0.12890692224634864 0.03295845462918059 0.09888495105724289 0.026726904830833804; 0.24334331112916202 0.14360321001635534 0.03179584196936906 0.10657949128326379 0.024300129929880725; 0.244809355400522 0.14451449562252794 0.03564653422818041 0.10791701776644867 0.02280936489578122; 0.24238014504315017 0.1478480712504485 0.04297154298532372 0.11018396280496344 0.023447753539292286; 0.2511936746835832 0.1534543646122057 0.04304963495221428 0.118193582592718 0.023858713473366315; 0.25412600817681347 0.15834025841911942 0.0449637700290417 0.12187440466746663 0.021904075162996146; 0.243040737171181 0.15203194758860517 0.042838086519315664 0.11801517275464514 0.022824155255070762; 0.23924160632229483 0.1460258504078249 0.04498776730591045 0.11395114872846587 0.023582881387203086; 0.2232759168365529 0.1355265162647136 0.0420261907016753 0.10639792701795565 0.022655260991954126; 0.2291587309534495 0.13551108000758233 0.046573827162227535 0.10416774319565192 0.019966757491750177; 0.22934427690467396 0.1368422256555791 0.04804986948358338 0.10471767826442635 0.022018369740663096; 0.24137251243560442 0.152179152500362 0.06387497075070794 0.12049113129428797 0.03414079434189647; 0.24201915395712004 0.15340153633096282 0.06372662305966899 0.1201384656814875 0.038737748406437636; 0.25016382918719565 0.1602427165392118 0.062441926063187 0.12617276554808154 0.03767259391515064; 0.2584855007009833 0.16096461917424815 0.06005384295073118 0.12757156447970974 0.03757716171835747; 0.25827232375757925 0.16354677959652436 0.06714798127720328 0.1328194769732484 0.06544138950423309; 0.2499011248351497 0.1559127967307702 0.05618618197329499 0.12248751481472084 0.07921313712847955; 0.24895115315924984 0.15156308915215613 0.04761886169433719 0.12165875105141505 0.07124483164034467; 0.24744517600545013 0.15607682749428653 0.054083551028729485 0.12421806250475967 0.07427798321550831; 0.24192143576152106 0.1488237689717476 0.046054129101324885 0.1163067527172019 0.06717264069680964; 0.2521557537460882 0.1527967699991754 0.05588623626827304 0.12246251464343466 0.06385658513358908; 0.23733602386669783 0.14454543629305294 0.04743054137914662 0.11600634593134242 0.060176306363754886; 0.2391429418083546 0.14539252252592033 0.0454217203063908 0.11711696943334832 0.05588062253341152; 0.2471964914605234 0.14804498876105454 0.049810222395510896 0.11780008105986989 0.04992451821661054; 0.23829938443543225 0.1390762196975605 0.04314073812127227 0.10912239991469126 0.0434535166265254; 0.2459480760259764 0.1426569296517099 0.041901608436585386 0.10994711572204384 0.03791076481474914; 0.25145399552689685 0.14739705611055096 0.042661068939591186 0.11371863229492786 0.04058085587726814; 0.24162296042527112 0.13985920539526145 0.03576399365588009 0.10734725420411018 0.03565097876574025; 0.24145454931803825 0.14775051348231633 0.04696831388889931 0.11807937363573381 0.03967765790768802; 0.22494476750332737 0.1341922013785235 0.047484049964898294 0.1063466049912649 0.03831898925740194; 0.22848328721395036 0.13450326254572803 0.049376336798233555 0.10517318071389815 0.046593884690909956; 0.22334530172245426 0.13205152933284708 0.04372194404614987 0.10309156097145573 0.041027897771644097; 0.2216685113707918 0.1297570228337055 0.04566789116631366 0.10265703701712049 0.03913934438542326; 0.23159971216517594 0.1409873354243283 0.04079706054862672 0.1080713049867738 0.03498732300890128; 0.22473090393700526 0.1389379491652683 0.03575880263546175 0.10404466847968012 0.030689150485735263; 0.2408546467889017 0.15003684383596066 0.052479493592572736 0.11558034428272176 0.036412865981134676; 0.24273286742120315 0.14893576381178764 0.05790960876098675 0.11400607652118626 0.034850303184726164; 0.2476671575081295 0.15385575793244097 0.06703427205841861 0.11785312634031632 0.046355721435338906; 0.24423094499682954 0.14763899755126358 0.060570600293963134 0.11082818868812448 0.04300288661332182; 0.2533040794418301 0.15670939871983625 0.061651977032732154 0.11962268462226014 0.042295841060171535; 0.24996624610313142 0.1534074929500969 0.05615494346047337 0.11912957249438938 0.052087011581333484; 0.25895879047305076 0.16276375151835693 0.057196423722703414 0.12553707395677707 0.05503391833756129; 0.2659649104054029 0.16397107797593125 0.05995084519259068 0.12642615345863456 0.05516438324573644; 0.26239649654827557 0.1636730882146378 0.0593828334416702 0.12905446038840576 0.05509638524510867; 0.261555979263004 0.1630194159442917 0.05531171999420759 0.1282395315861572 0.05428054495818143; 0.2548728363603086 0.15139228777843597 0.062184845741955735 0.11710024666356 0.05193533178501705; 0.25758378520725017 0.15383497716393377 0.058184419342969494 0.11856792602194907 0.047417982206411205; 0.24990642321203427 0.14960745347663804 0.057321229989603865 0.11620389011107733 0.051869604516559475; 0.24609654150084082 0.14943678377568756 0.06634956899505909 0.11882943281811754 0.048689111146158884; 0.24641719263136724 0.15030203520059612 0.06597724648890539 0.12299413378463014 0.05296274051890922; 0.23499547681284222 0.1433423201942446 0.06292996331117665 0.11755983200014293 0.04655085661173783; 0.23722051672992922 0.1415742727680208 0.056461398370560925 0.11558247241449882 0.040792615478522955; 0.2242027121214693 0.132244276906109 0.04887643335163348 0.10817741807756844 0.03661765929284682; 0.2203390099548201 0.12748961381519328 0.04562819503068728 0.10280479207800247 0.031847105569922846; 0.22756260815802418 0.13132357484026344 0.04479579579686962 0.10531130802763636 0.033912397342748576; 0.21755393889382046 0.12370291112600637 0.048373347138212855 0.09849517343150087 0.031001790895324656; 0.21888934311735284 0.12324123190831242 0.04093156381634612 0.09387186704243428 0.028910840677628287; 0.21074085424318037 0.12232397730740784 0.035292481997114336 0.09689450542660719 0.02752125807297974; 0.2016364941197564 0.11868770607783698 0.036717726285061765 0.0918693326356583 0.024246390977543587; 0.20948033405923283 0.12396263331949157 0.03407109595422071 0.09640124946376269 0.02504301225665569; 0.2175397157556489 0.12917171419286286 0.05142130756047663 0.10273775267235902 0.03059386287548828; 0.21477546333366035 0.1305199027111018 0.052834370413758734 0.10722924616044734 0.03314659828479041; 0.22606966923946856 0.13631003082194998 0.05366204400208662 0.1115353929687021 0.03525465421505729; 0.22460765168090435 0.1329984524281746 0.04838205725429114 0.10586760959533675 0.03459175878864892; 0.2177301418782852 0.13084595866457033 0.04659316048405692 0.10618052946732698 0.035997419936278405; 0.2201556560994452 0.13157211714947548 0.046082888636049625 0.10563024534548329 0.03248123924558873; 0.2176487801552825 0.12814287472934982 0.044263805373952386 0.10075947814198341 0.031629316935940704; 0.21980227991589013 0.13298925164676872 0.0392234072978859 0.1080771519582431 0.030951118438445824; 0.2306737638683963 0.1359447402027223 0.03956330187285462 0.10722705295411432 0.030874369566840566; 0.22356435355916404 0.12899373867249278 0.038599222091154406 0.099255802796107 0.028059550667963534; 0.22649413106739347 0.1380786033323271 0.05002427334572168 0.10942156518763023 0.03535234713169901; 0.22227765427350857 0.13289226099656923 0.053583559771261946 0.10529697164110913 0.039462851503395784; 0.24756838525390512 0.15956250631655775 0.06110944092661725 0.13031809508174716 0.04829966139308909; 0.257439006527709 0.16236247761126774 0.05718407598448266 0.12790551119542168 0.053117701800762016; 0.25577963921264574 0.15547944520375265 0.05304096568475143 0.1228790707071308 0.05273058192300669; 0.2539812686668695 0.15780765048234568 0.05081133115371049 0.12666893714107544 0.047539603124998976; 0.2337752898634959 0.14529672300075613 0.04241547930453206 0.11614662379771448 0.04159339343881049; 0.2141865597249261 0.12996050594453115 0.03792520211211033 0.10257615498304348 0.034820833625151225; 0.20656276592264106 0.1223187615728704 0.03529233909504563 0.09628630708932862 0.03297639333447099; 0.21167402345855657 0.12384371322443706 0.04120863419260144 0.09759083613777149 0.03322900736920262; 0.217642575533546 0.13200003991167245 0.04812752011605549 0.10606063783187857 0.03651823623651047; 0.21522163453209955 0.12673593582423923 0.041388425777860074 0.1008712490798568 0.03650264336604897; 0.2125331121882483 0.12617548324038502 0.040511908223635026 0.10092297865164561 0.037438851497086076; 0.23468868996307726 0.14292630666390987 0.04384529086184984 0.11775645552644953 0.04090284905951197; 0.21448219868028542 0.12839297891772533 0.04341168968663601 0.10627562429364383 0.03781786356565138; 0.22538802268095318 0.1359278346388876 0.04877641265619586 0.11271041235014487 0.0372659197485191; 0.22382809712082152 0.13563303135151383 0.048243064652115426 0.11078251133906594 0.03878209638879636; 0.2338944474346638 0.1410808224067268 0.04451931359984901 0.11440649017133515 0.03988769569624216; 0.2292519588857651 0.13829700617672422 0.044611561289377426 0.11433587181121668 0.039856797555118804; 0.24117521084068302 0.14970889960671596 0.045050940804439714 0.12132840420842617 0.04152968712570668; 0.23209364026163487 0.1406700171029181 0.041673412063922825 0.11255792233181355 0.0354706654358697; 0.23217180418471073 0.14019997175499682 0.04034690818326182 0.11168910475836086 0.03558463156491853; 0.2384416166742609 0.14810776814591792 0.05617356358875042 0.11876472761047592 0.03993924126243859; 0.2339630934635771 0.1452997692805283 0.05312971370545392 0.11658530775557129 0.03787179385297513; 0.22229839468319992 0.13514638341520252 0.053702716307857556 0.10728127732952569 0.03381125219899826; 0.21703182144419178 0.1338656009996257 0.05274782371681446 0.10820761948887614 0.035385919815209804; 0.21489582346642672 0.12867222174122506 0.047614704780074076 0.10108279341510222 0.03408656462006354; 0.2168986331364684 0.13402478551160948 0.05677997168882061 0.10852410419028032 0.04198840265649624; 0.2114444687717098 0.12600661490592685 0.051535790315138254 0.10064876644405546 0.03756864000501686; 0.221466512660419 0.13577302137401365 0.04936868659724152 0.1097680226452575 0.03980927768661542; 0.2177030930362026 0.13053450258085458 0.05688307851210718 0.10659081552326088 0.04524900349628101; 0.21198706940347992 0.12264019317634367 0.0524618688794413 0.1000142251563025 0.041708627006619536; 0.2071513344091975 0.12459212296968669 0.07157049982328723 0.1050669584760628 0.04391780587928244; 0.20577807400566764 0.1238693605165956 0.06637736858788737 0.10270116898135835 0.04188949837602575; 0.2039769146755729 0.12050927065223674 0.06530086384704596 0.09935209193004366 0.04339044719391981; 0.19174326391342436 0.11324488973546204 0.056979713705109646 0.09289152354537007 0.03879417360885079; 0.20393213773825292 0.1220678347820296 0.055904052946509596 0.09948151255081937 0.04007927159319826; 0.20242672379858115 0.12087995825006598 0.05498271046562328 0.09839944000586545 0.041388534147346084; 0.1925240722580498 0.11262590799962706 0.05038392828689682 0.08976303502356749 0.03606055874232774; 0.18900677003731295 0.10852542660025935 0.046984857364787004 0.08568242114333902 0.03643492469075779; 0.19267134518043172 0.11039389931272015 0.04594079736415016 0.08699426886676624 0.0370817769279755; 0.20652178645623503 0.1201395800758246 0.04348733466699495 0.0927709958929926 0.03754764854595477; 0.2051658806840005 0.11847119915873555 0.042164582048533544 0.08947210039529084 0.03845827999461027; 0.2070609055073597 0.11389788797212241 0.04916664901151513 0.08845295628573797 0.039578901014712106; 0.21937945064795317 0.12727470545540331 0.048688383690708915 0.10156901674005431 0.03644884926635953; 0.21827871463213208 0.12498969017322921 0.045210529798026124 0.09694521374728712 0.03180092639771249; 0.21878022342136577 0.1295585288910553 0.05450587177972415 0.10440638559839274 0.03272928797838804; 0.2407729597028977 0.15492494935262083 0.07714843018611604 0.12798416831319448 0.04862685752819154; 0.23006214270090153 0.1483966944374075 0.06718856740502782 0.12219675803760621 0.04590339340098837; 0.22832491154746287 0.14473905366718215 0.0630869492273193 0.11786665012105253 0.042590749903147526; 0.22176218255580324 0.13708255401896988 0.053316238659573516 0.10993886879812835 0.040213423584799055; 0.20397754787779537 0.12540519356050137 0.04533451877322032 0.10051270686969088 0.03440562955232468; 0.2016267450998361 0.12096022909337714 0.04108407302030908 0.09513921231734694 0.03491138475491211; 0.22467195767960035 0.14170067684216844 0.05008093677623261 0.11647987318601562 0.042982125241387725; 0.2310512763563878 0.14354033709656036 0.05073703035841933 0.11826105080100976 0.040761200752917004; 0.22036449828180366 0.13808259470137627 0.052948671222770624 0.11009915649535723 0.04233357015614754; 0.2075821685269093 0.13024481318690515 0.04957282455050501 0.10203420901014382 0.040877752628843356; 0.2147208752214603 0.13645854240495472 0.04569668699330928 0.10948470659028668 0.04187063103073467; 0.21863866762158812 0.13285232202878403 0.043306475164706246 0.10644869100627247 0.03703353497011366; 0.21290465129087402 0.12890084279911365 0.04403206827816545 0.10471213731429532 0.03751523970661881; 0.2180036310964428 0.1297220066653621 0.037800656674422256 0.10428218492477381 0.03349715017555811; 0.20817623473116578 0.12243972722426509 0.04180031496732825 0.09850204099106187 0.036474969333638016; 0.21098325401074747 0.12157022061932449 0.045747289386982866 0.09835754421462532 0.0378658533861075; 0.20647656321149715 0.1222173574804335 0.044212937317367515 0.10051754037229155 0.03578176683345112; 0.2109933358400794 0.12399422254078143 0.042863213985821505 0.10243810798476485 0.034815658320257445; 0.20564521646259087 0.11596747091144366 0.03849401814314596 0.09578529664476988 0.03397561830919534; 0.19392659799860207 0.10940807293438946 0.03243314065345424 0.09083114201704882 0.03029922908160329; 0.19261082042540145 0.10584095403022795 0.02910048485047259 0.08709069945319671 0.03228915445497227; 0.19500135901995527 0.10454879182153726 0.03043539053397686 0.08756387865864577 0.03437035650007401; 0.19214042642456713 0.10872811855931111 0.032179155756611115 0.09158789723176433 0.038616919726073534; 0.1964377730587516 0.11041467960325105 0.03066811553901711 0.09165997492518961 0.03889046596283896; 0.20167329366997033 0.11468506118176161 0.03644697466306908 0.0949468409001584 0.03846188177104937; 0.18931260570681216 0.1034288486680808 0.03010186929554163 0.08429128537414513 0.03642909756848134; 0.20421928655939198 0.12106697009733694 0.04158010635018681 0.10145699270437591 0.04075553541619712; 0.2022891858564766 0.11840822495405974 0.03845683279228476 0.09854255646761603 0.03867495390466161; 0.2109050388611914 0.11954164910225154 0.035260081878044344 0.09925613278386074 0.033687963186731396; 0.21691551589787494 0.11962212797330285 0.03517421307423761 0.10001035709569515 0.03443021181148724; 0.21481030411577617 0.11911227843226166 0.03684589095718901 0.09963815305145313 0.03273527468083252; 0.20404880028610542 0.11343034886170364 0.03312306677049192 0.09486648157049599 0.03689528595279017; 0.19404879138187658 0.10609875297823697 0.028859516516791122 0.08746094849554208 0.0324757256626714; 0.20164457500232133 0.11774223189575792 0.056692199337853064 0.10047064599869654 0.04584846266266733; 0.19713420403204657 0.11310725721536732 0.04831408226758088 0.09313248000524844 0.045792955105757954; 0.19213660047215064 0.11036964406823045 0.040513224392293656 0.08930963944977448 0.04106450128675004; 0.20617538679251543 0.11884187380675415 0.0432416695766916 0.0974249058690542 0.040853444869283835; 0.2303230105925359 0.13799494381907734 0.05169119325584333 0.11226273784851026 0.04586343348818143; 0.22909363322168652 0.13453651121189716 0.05280623594765791 0.1068951375072399 0.04057740772403971; 0.23425229162144712 0.13851232449953177 0.05149987869338138 0.10899786049407317 0.041141485261024596; 0.22375811851158184 0.1313135280866974 0.04881726330817495 0.10547538961395896 0.04707498060631876; 0.22495265774833711 0.13496733543551392 0.043266538044220246 0.11263702603519182 0.05626424069776634; 0.21756652373399377 0.13005571434717517 0.03805354496670249 0.10846856965494331 0.048962726393934085; 0.22601302566787435 0.1421163320129803 0.04349019138679888 0.12166354345379016 0.06049577977227846; 0.21709805609910357 0.13266609128997256 0.03883022325170824 0.112108605401498 0.056781345544001896; 0.21465711499952211 0.1339083394740862 0.04389822240219743 0.11277855221174711 0.05546448494016444; 0.22607708736819374 0.14370149722376208 0.045480567509303335 0.1184948655664329 0.052924752404445934; 0.2334056855405358 0.15528314094288143 0.048140261705215646 0.12852258465285335 0.051917945728822176; 0.2326311368676017 0.1514286719206412 0.04932781041502624 0.1254144672083476 0.05192696880191455; 0.229774797871271 0.14525349914578115 0.04588388437700009 0.11882258115431617 0.04710044987213524; 0.23940395308697957 0.15489167952177932 0.056936448591325566 0.13029190228955706 0.05186933648357321; 0.24502079878779046 0.15932966060350742 0.05249895242045235 0.1323455280190846 0.0464928634208006; 0.2375181581142091 0.15010551541575118 0.04943171361835727 0.12188719708729909 0.04624883828493455; 0.22839751267930217 0.14565872096640525 0.05108241464497192 0.11798160323706568 0.046965607239266224; 0.23725026388565976 0.15582737977204847 0.0552112199926499 0.13010752041504622 0.04594347758766809; 0.25450168482144897 0.16380395515678825 0.056786820337305345 0.1368114458669491 0.04712086277148564; 0.23248785679880957 0.14689612655972245 0.053083246237142785 0.1233450259486252 0.04503572966211192; 0.2273757840819691 0.13877060776261332 0.04995129528530749 0.11475054557875108 0.04088221454066556; 0.23694258416712558 0.1425597023193665 0.04707212217957427 0.11573928603136788 0.04599655390534815; 0.2249467123351119 0.13574638575113834 0.04075056003678362 0.10878886587305267 0.04345327443483684; 0.2256825396459597 0.13977566349345066 0.04690421273031649 0.11375895982490698 0.0460899011421459; 0.2272667033705153 0.13428126712908442 0.043266825698564985 0.10887466297949727 0.043639985859652924; 0.2052725066330463 0.12095784745828386 0.035675390228083165 0.09843265132232806 0.038843923446743145; 0.2330659536191964 0.1399632183886852 0.05155571294979289 0.1208900411218349 0.054052857468293865; 0.2240519450242634 0.13388942733822554 0.046569992050775166 0.11152157728194746 0.054663166232718434; 0.21698994347535094 0.12828627521132063 0.04344586522002878 0.10632343724822643 0.04748205901409261; 0.20891075558727998 0.1226732724454771 0.038324246605196496 0.10102052498225882 0.04361589227100272; 0.20022135656886117 0.11388975032542312 0.0322396099219393 0.0941417967944504 0.03762706478867975; 0.20912050947994246 0.12020231801966161 0.04476792332726091 0.10126219734900484 0.04664375720766423; 0.21988497174143992 0.13120384529192708 0.04590996775783991 0.11096943652910621 0.04906917284605692; 0.2212183077840821 0.13232800376383036 0.04537300431734638 0.11161935566888356 0.048688131685477816; 0.2250243286060346 0.1445092202184007 0.0606373402596022 0.12343811880768223 0.0637842992865422; 0.22430386322872264 0.1389034060404623 0.055600834885875805 0.1164378693995546 0.05825888429469892; 0.21110462191213308 0.12285192427165703 0.046966294099601444 0.10237702226024237 0.04867872274428232; 0.19984343483057926 0.11731799039941944 0.04551530725734419 0.09834069059595558 0.04285985495853125; 0.20870948301956901 0.12488172724804812 0.043781924273387486 0.10556045807445123 0.043670587867162214; 0.21963168157900056 0.13030901372402137 0.041279020329964874 0.10681863188381255 0.04923958679410743; 0.2099275994202668 0.12523960626100877 0.03989853380771694 0.10378766852327394 0.04931480045416297; 0.2121060784976621 0.12652242128829463 0.04165377949597214 0.10191163905627097 0.04513008243579342; 0.20508806676236307 0.12052694366201007 0.03629007166065196 0.09736290813022108 0.04071923906496107; 0.21414401746247225 0.1288633050984084 0.03616690467148955 0.10764478338188531 0.04063831644170236; 0.2175179898059687 0.12631526310967917 0.03125287941873023 0.10577244166474821 0.03553967849940262; 0.20931114787390398 0.12183361724795909 0.03737977575683553 0.1009379270986023 0.03570316748047035; 0.21254898734514371 0.12631848633910825 0.03534229479868379 0.10614381876113434 0.03409057756741175; 0.2105826388011333 0.12540778363248198 0.04163512593618367 0.10681326058723464 0.03752117450419529; 0.19670847258646937 0.11427282567421983 0.03851067912965086 0.09610838685208904 0.0428015964856423; 0.20325475495401743 0.11991684755166682 0.041026811191551424 0.0995393817128686 0.043893192917559706; 0.20675958344414808 0.12184381680075575 0.04558356186875704 0.10180366581693871 0.04420580567753646; 0.20302636642515642 0.12065186507609883 0.04702552397949698 0.1019855542660998 0.044251246317913794; 0.20133636668729768 0.1156152290670665 0.04034834030442002 0.09509190250883474 0.03886433499728891; 0.20961121738281238 0.1148979417537524 0.03723684773880293 0.08873974147995292 0.036124338171285415; 0.20456112242004387 0.11354054477253545 0.03280437965771 0.08902875026909493 0.03264921699377062; 0.20242993288247674 0.11615327271969308 0.039834329820318544 0.09449531488297766 0.029913437595265407; 0.2186435620229156 0.13322164633394235 0.05344795730641963 0.11030883473299652 0.04632623124543611; 0.21953105411853083 0.13180730456925197 0.04664243546669866 0.10853205726260114 0.04683084192612794; 0.21840842550536543 0.13294378491097103 0.048603388468783586 0.11055802637906208 0.04184672767610571; 0.22600853829018713 0.13557930745167263 0.04655289872516115 0.11128738738752472 0.04119420849038141; 0.24731667946523384 0.1615667439101754 0.08138645171347395 0.1393280761850442 0.05981749338112653; 0.23190578707652057 0.1505176501749848 0.07259744265058148 0.12880262632469858 0.052475877814113156; 0.22579959840454072 0.14582555610171116 0.06125436126393881 0.1243992350443246 0.050018346876000604; 0.21836509156924416 0.13606004014198905 0.057644880258661955 0.11620970185153023 0.050130350148753514; 0.2051724729832167 0.12382301962045769 0.053346583897767426 0.10587709935945143 0.04663369179254865; 0.1969853262421413 0.11463878522847445 0.04615363873433905 0.09465397729430094 0.04516228458671645; 0.18684792183374752 0.10762332853106142 0.04346192794952263 0.08995465057256616 0.039806779345980293; 0.18117798596648682 0.10347671142361546 0.044725907438305776 0.08815648897220926 0.03754129921087504; 0.1916889407636985 0.11511690681093523 0.04938379036848367 0.10034541880075325 0.040305423058580404; 0.20237329370993493 0.1233993124160257 0.04585881020597316 0.10503563360360614 0.039283630603560646; 0.18802520745768642 0.1112205600693295 0.047367833194905104 0.09497370854804796 0.03349499436289775; 0.1910177359086235 0.10913959222670155 0.049708655188698436 0.09127181399496302 0.031833952175146; 0.1981575043282477 0.113979253789868 0.04823160252787182 0.09298182579781139 0.03832495650177452; 0.18450338254623158 0.10418359627015278 0.04389953156763323 0.08418637009784002 0.03412758834580781; 0.1818644244293574 0.09885778925567376 0.04400017939372069 0.08109714879452722 0.03023386147554876; 0.18584803253970172 0.09946990680098143 0.040552228226170585 0.08256612156915295 0.0284256611520939; 0.18230347741096517 0.09913846340894386 0.037714007871473346 0.08252332059611978 0.03084051255423966; 0.19623071279882828 0.11110485980605828 0.03800162494351428 0.09209898172275305 0.03464471265903428; 0.18965988716887983 0.11066619815187254 0.03230664512650141 0.09244978027308845 0.03931494277899515; 0.19817614643897652 0.11977186311687309 0.038768929291852064 0.09973346568556518 0.04759926972536287; 0.196127025001256 0.11595566627904 0.03844782177534719 0.09595682126213623 0.04161741636393898; 0.20097359237115253 0.11291383848606923 0.040825759829497495 0.09121172300521146 0.03692676280199236; 0.19609149668249026 0.11367291129445535 0.039435277749233374 0.09257134931519517 0.03807473975824314; 0.20052560666110147 0.1160354488437613 0.045685277179187876 0.09507613738167198 0.04895507135714688; 0.19788054723664944 0.11754211521905582 0.0532827547552636 0.09821713206996847 0.05440969289323169; 0.1984685567945228 0.11470098435292181 0.04500834906746553 0.0966884572333521 0.046765527792616515; 0.19802313609361538 0.10769231628902386 0.038216887655056375 0.08727341102770379 0.04014953439114; 0.2032857204551688 0.11289107808691366 0.03977994371827194 0.09378200586407512 0.03880741468809053; 0.20915598293743065 0.11790454693017088 0.04481936643024881 0.09581892940019869 0.0407258326052984; 0.2109166701285166 0.12107340341709202 0.04226388503710905 0.09795529546431941 0.039293647397705744; 0.2069691673634944 0.11895203368586021 0.04497167841275914 0.09895422728532348 0.0380883154484819; 0.21156269556033594 0.11972951413569227 0.04056265615467535 0.09901459701199368 0.03452414259518708; 0.2057273198822974 0.11103726543090642 0.03758158900276269 0.09241533428302634 0.029529171505713665; 0.20663171387989035 0.11168581837099315 0.03339664483416435 0.09408482283251467 0.030862316097135706; 0.19904662173810572 0.10708315993294336 0.031256538882639864 0.09035989290393974 0.02717637723610033; 0.21107955179073787 0.11910535951411896 0.03163354327661742 0.10280494706565209 0.02836858470976535; 0.19844105761415462 0.10842948553924699 0.028621103955371766 0.09223230732865388 0.02861503168237355; 0.21110960778527815 0.11527752099804035 0.026460466806541755 0.09750186793714567 0.027507218578792784; 0.20116286227650132 0.11194046263593 0.02391076210345894 0.09534115755724751 0.024772281609445553; 0.2042453308864171 0.11530712584414134 0.02306715087160325 0.09968646348848217 0.025103424370264804; 0.1910266504656263 0.10603838385945995 0.02165113773298149 0.09095523143875023 0.0217006673455046; 0.20541099317637984 0.11336920238976828 0.020363897734200036 0.09591411956204907 0.02008859432308327; 0.2115586060902906 0.12292745870308201 0.019153119770340187 0.10358227318965543 0.021413149245130624; 0.20556943683794598 0.11716530004704889 0.021625061152499566 0.09789319705123226 0.020674712529816314; 0.19858359848635562 0.11372816784830807 0.020179917928573807 0.09357228127046045 0.018748419763476118; 0.19779409710707002 0.11299432544828986 0.025930744323728334 0.09297405925928447 0.01935438546087779; 0.18001452282382438 0.10298147135115888 0.024346814831970414 0.08271583838295057 0.0176213572898224; 0.1971210614467731 0.11849606699257872 0.028178896282814565 0.09875510273799193 0.022122375903822183; 0.18567217891415524 0.11209362529921357 0.02511347066090713 0.0932552115195981 0.018956709376859428; 0.1822354525725092 0.10554282492961743 0.028143562223324856 0.0871446884531968 0.017728433164467622; 0.17735960129102432 0.10216219972822077 0.025557464797444886 0.08307078237209266 0.018656434239951936; 0.18043274119059532 0.1049794485271216 0.023471422954219775 0.08726834012964206 0.01723523157100532; 0.18301366912969186 0.10300969223978046 0.024739420782580533 0.08389264844972959 0.015832167479480533; 0.1859706125469862 0.10690645190717318 0.023829864185893185 0.08775554103151217 0.01835512771255591; 0.20476061159863937 0.11756218125535281 0.023702956986899094 0.09917484722531045 0.01691053476917202; 0.2058291052142371 0.1217069766927817 0.02546513249673439 0.1039173002203004 0.017158449402351814; 0.20196718489007864 0.11883317615660496 0.029215620320622068 0.1013642560569204 0.02235577162973057; 0.20031369439662863 0.11782460459925706 0.027926013955739293 0.10236592232209502 0.026891081785138216; 0.1874886301112284 0.10700062204486509 0.024643123084221008 0.09140422355351495 0.028224933300396417; 0.1876008359155742 0.10551759085326497 0.024317927606037237 0.0886960176524929 0.02706037526149004; 0.17966234664612513 0.1011454332373071 0.02694996665686844 0.08538216782787734 0.024493100823012585; 0.17122783943409522 0.09472105948142436 0.027128969397310243 0.08009982229812379 0.022705663184164046; 0.17910260009284656 0.09615897773116609 0.025908114451101485 0.07948577649627872 0.019763052241872213; 0.19063082673164877 0.1054872543685419 0.04485640828842406 0.0886244823315521 0.023353864075239865; 0.18101423651387433 0.10154634335222106 0.03746149625904945 0.08609740831683317 0.02488554910540292; 0.18376991486875327 0.10318549121286281 0.03421100141328643 0.08639046717270404 0.029392747497317864; 0.18612818687222887 0.10178475644084461 0.03603342775878962 0.0831389798210795 0.026597434513376296; 0.19301907932013265 0.1047676116497727 0.03845099989078567 0.08641612517728291 0.02389915350684018; 0.18248352877497667 0.09889446677934423 0.0381367346326679 0.08135970374261443 0.021275332516797314; 0.17972894090175623 0.0974603825384084 0.03646826371989012 0.07932073823861364 0.018924944358164414; 0.18467375101852412 0.10142222264001399 0.04128649384134102 0.08626186263364222 0.020950249414320266; 0.1731057809766769 0.09434558326871896 0.04489134490770569 0.08059411177477571 0.03011650966062186; 0.17492208556148525 0.1031976302454607 0.040940476255873604 0.08686591728084352 0.029850443464152318; 0.17870397508790584 0.10369559208470475 0.03509694833339037 0.0850246418003485 0.027702995473450266; 0.17017180634061888 0.09960467978253279 0.029945157706982146 0.08276908544574144 0.025608795054201956; 0.17361565361436523 0.10362801294671944 0.03321189303417703 0.08476033715704252 0.025677594029859443; 0.17623123272273 0.10620839568891088 0.03629994959012429 0.08725534753639833 0.024110235012734522; 0.17989541684796853 0.10775268264943727 0.03510333864689477 0.08979350478759873 0.024062107667060368; 0.17463019565908466 0.10143807084031398 0.03450207923889643 0.08363821030705348 0.020560138486857553; 0.1738252973649371 0.096433308129847 0.031333674113277483 0.07866466454505265 0.019196547456511132; 0.18567301321772484 0.1041905940813541 0.03804310291633915 0.08706235467862558 0.02048798753355207; 0.17001096746323704 0.0959618706498718 0.04114866980613002 0.08109970578131256 0.019814916777883065; 0.18162604146002292 0.10266438277516172 0.03778781762183292 0.08590844125411652 0.018296875904122267; 0.20390622395514296 0.11811003805759275 0.03998004065323339 0.10166782916277045 0.020855536614949922; 0.19871353867243804 0.11382307238628644 0.03449001686617506 0.09550985271286484 0.018273097966190515; 0.18168412854346497 0.1052216152528936 0.033535529017208195 0.08895247240504835 0.019127756014725637; 0.1745781239674319 0.10006485066255048 0.03311402059774254 0.08498776403777769 0.01857596831938511; 0.18214553092367086 0.10545202737204326 0.03159496998533133 0.09115191606849807 0.018204637323187875; 0.1966084916945031 0.10998251454156313 0.030928966180439978 0.0918633063290149 0.017545808467759362; 0.18980399406399173 0.10780695957836846 0.026439634010955643 0.09002061195402385 0.01719136788526668; 0.18952527552005324 0.10530632839916022 0.024568461141598184 0.08760791873716546 0.018221162043646922; 0.19157756494805556 0.1147619583711455 0.041656251459608044 0.09981599931544646 0.02860948426138238; 0.19649386407792838 0.11606739350203116 0.038057735877664534 0.09897259262900818 0.027542893450346592; 0.1978644460587523 0.11475580096676699 0.0337757559408201 0.0968049244101943 0.0273295817163682; 0.2005289965986269 0.11797458160269064 0.03798132374202833 0.09831256725518714 0.028792003483541488; 0.2009094972705092 0.11739657106675945 0.039937451357170944 0.0987229863455201 0.03004608402925148; 0.2025171891288158 0.11764415528518551 0.04002450918120146 0.0987457956592484 0.030184825189132805; 0.20004500452170346 0.11327757081304068 0.0346352737344265 0.09374553616605152 0.027315096747652146; 0.19000406566055278 0.10600244216850657 0.02891340255315781 0.08819464817255299 0.02781382188540733; 0.2029928207619322 0.11894349724238124 0.03549486815592194 0.09990175246882088 0.04241035568985967; 0.19934363784180742 0.11804345226434872 0.03508663436500664 0.0979968562101336 0.048342010881691204; 0.1859738359593285 0.10683622117756211 0.034912772313582384 0.08749233270684972 0.042435303658198545; 0.21033812600318055 0.12733684107397716 0.049802073705854 0.10686969824632084 0.04757348474260269; 0.20403209557488333 0.12003569453743873 0.0447306111156241 0.09814649576346139 0.04895799553510426; 0.21662845198595343 0.12638492703269147 0.04776225236648686 0.10790321333726294 0.053283096421693786; 0.1988561162096963 0.11517262464626807 0.040409136916950285 0.09580092810408312 0.05119741569474143; 0.21331820557456854 0.12584778373133482 0.04796655504366154 0.10792788213742605 0.058197103822348925; 0.21281500693115907 0.12289861951026393 0.05162416123120303 0.10591912346087162 0.06751445264348857; 0.21948679217460407 0.12320299288632927 0.05408947992538067 0.10681124390762857 0.06276266688688177; 0.22405319852640354 0.13054159157278106 0.05984419497422101 0.11666048456511348 0.06949241490827861; 0.22754469965307014 0.13921266693116796 0.056566510399752634 0.1248656850201404 0.07276438648833325; 0.21643481913731968 0.12679182657195387 0.052102480868954484 0.11262289761642741 0.07558847745524637; 0.21846985032976848 0.12642483944569632 0.043105647502956014 0.11136024855884018 0.07649767820252412; 0.2146405932173823 0.12303639181355322 0.04564224300870675 0.11033473492314101 0.0692120235599155; 0.2223210022342757 0.13301315886099882 0.04484320451290908 0.11880634093800926 0.06588170485195118; 0.23024934414963372 0.137487056710877 0.054894469833147545 0.1216419258874237 0.06597682232854046; 0.21676646974834163 0.1252599500485722 0.04957788561743261 0.10839160485359665 0.057787426597454374; 0.2165808563006112 0.12514505478687793 0.044860507050846106 0.10723919384314726 0.05258116635606943; 0.20874456739999367 0.11811645730692315 0.03862637461449232 0.09874008864270933 0.045254470013986095; 0.21281155984860667 0.12021115147557392 0.04277413109918854 0.10032630479421051 0.04211519038451518; 0.20903759631524094 0.11839370358774291 0.04170547838990228 0.09897223376103903 0.04191160749016448; 0.19417200829990394 0.10949456784160318 0.039076623273764745 0.09027436808044645 0.03905827915166413; 0.1952680694771424 0.11525133624101783 0.03802412133644001 0.09768436300988938 0.038717488123930256; 0.18704179904561163 0.11120621114512369 0.03651453770681203 0.09104411610552426 0.03450619825637878; 0.19435361807903384 0.11604303717247712 0.03543735542880679 0.09521963841588303 0.03216558527582122; 0.1974600317904213 0.11491837680047406 0.03337272007455178 0.09560614841676557 0.030210327881640058; 0.18174574874471497 0.10289010518555367 0.028899566884853428 0.08337950720387144 0.025586255966328277; 0.17916168552741107 0.09683783144763726 0.026414157941753058 0.07772346150078331 0.025320858993095316; 0.1875114791163182 0.10321981442778602 0.02398493671998532 0.0832740689213908 0.03005373054779542; 0.1912628871256809 0.10261613712953961 0.02670468516814829 0.08220860559907248 0.030062528667147738; 0.1944386581225952 0.10319367964067011 0.028001673044110307 0.08400856414768448 0.02792071503781937; 0.20161792295326872 0.11142384842235206 0.031864352143879705 0.09306063421037475 0.026604244107076826; 0.20957420195857748 0.11787338721909808 0.03476089804734864 0.09921229118082268 0.035670862789209126;];

In [20]:
A=zeros(size(res1000));

alpha=0.93;
for i=1:size(A,1)
    for j=1:size(A,2)
        if i==1
            A[i,j] = res1000[i,j];
        else
            A[i,j] = alpha*A[i-1,j] + (1-alpha)*res1000[i,j]
        end
    end
end

#DUMMY FUNCTION FOR PRESENTATION
classify_digit(x) = 7

classify_digit (generic function with 1 method)

# Example

In [21]:
plot( plot(digit), plot(flipdim(reshape(digit,(28,28)),1),t=:heatmap))

In [22]:
answer = classify_digit(digit);
println(answer)

7


# Results

In [23]:
labels=["sgd" "momentum" "adam" "adagrad" "adadelta"];

In [33]:
plot(A, xaxis=("Iteration",:log), yaxis=("Loss",:log),lab=labels)

In [25]:
final_sgd = A[end,1];
first_inds = map(x -> findfirst(A[:,x].<final_sgd), 1:5);
first_v = diag(A[first_inds,:]);

In [34]:
plot!([1,1000],[final_sgd,final_sgd] , lab="")
scatter!(first_inds,first_v , lab="")

# Speedup Results

In [27]:
speedups = first_inds[1]./first_inds

5-element Array{Float64,1}:
  1.0    
  2.19603
  6.36691
  4.09722
 11.3462 

In [28]:
plot(labels[1:3],speedups[1:3],t=:bar, lab="Mocha Base", xaxis="Algorithm", yaxis="Speedup (x)")
plot!(labels[4:5],speedups[4:5],t=:bar, lab="18.337 Upgrade")

### Achieved 11x speedup from SGD, and ~2x speedup from Adam